In [1]:
#Import required libraries and functions
from sahi import AutoDetectionModel
from sahi.utils.cv import read_image, read_image_as_pil
from sahi.utils.file import Path, increment_path, list_files, save_json, save_pickle, download_from_url
from sahi.predict import get_prediction, get_sliced_prediction, predict, agg_prediction, get_prediction_batched, get_sliced_prediction_batched, predict 
from sahi.prediction import visualize_object_predictions
from sahi.postprocess.utils import ObjectPredictionList, has_match, merge_object_prediction_pair
from IPython.display import Image
from numpy import asarray
from tqdm import tqdm
from PIL import Image
from sahi.prediction import ObjectPrediction, PredictionResult
from pathlib import Path
from multiprocessing import Pool, cpu_count
from torchvision.ops import nms, clip_boxes_to_image
import cv2
import os
import time
import json
import numpy as np
import time
import torch

In [2]:
#use the pre-trained model
yolov8_model_path = 'models/yolov8/last.pt'

In [3]:
#create the model instance
detection_model = AutoDetectionModel.from_pretrained(
    model_type='yolov8',
    model_path=yolov8_model_path,
    confidence_threshold=0.3,
    device="cuda:0", # or 'cpu'
)

In [4]:
#functions to set the overlap ratio and slice size as per detected objects count in each slice
def get_slice_parameters(object_density, slice_size):
    
    if object_density >= 50:
        #slice_size = min_dim // 4
        slice_width = slice_size
        slice_height = slice_size
        overlap_width_ratio = 0.5
        overlap_height_ratio = 0.5
    elif 25 <= object_density < 50:
        #slice_size = min_dim // 2
        slice_width = slice_size
        slice_height = slice_size
        overlap_width_ratio = 0.25
        overlap_height_ratio = 0.25
    elif 10 <= object_density < 25:
        #slice_size = min_dim // 2
        slice_width = slice_size
        slice_height = slice_size
        overlap_width_ratio = 0.15
        overlap_height_ratio = 0.15
    else:
        return

    return slice_width, slice_height, overlap_width_ratio, overlap_height_ratio

In [5]:
# Apply Non-Maximum Suppression (NMS)
def apply_nms(detections, iou_threshold=0.5):
    boxes, scores, labels = [], [], []
    for det in detections:
        boxes.append(det.bbox.to_xyxy())
        scores.append(det.score.value)
        labels.append(det.category.id)
    boxes = torch.tensor(boxes, dtype=torch.float32)
    scores = torch.tensor(scores, dtype=torch.float32)
    labels = torch.tensor(labels)

    keep_indices = []
    unique_labels = labels.unique()
    for label in unique_labels:
        idxs = (labels == label).nonzero(as_tuple=False).squeeze(1)
        class_boxes = boxes[idxs]
        class_scores = scores[idxs]
        keep = nms(class_boxes, class_scores, iou_threshold)
        keep_indices.extend(idxs[keep].tolist())

    return [detections[i] for i in keep_indices]

In [10]:
#convert final predictions after NMS merge to COCO format
def merged_preds_to_coco(preds, image_id):
    coco_predictions = []
    for pred in preds:
        try:
            coco = pred.to_coco_prediction(image_id=image_id)
            coco_dict = {
                "image_id": coco.image_id,
                "bbox": coco.bbox,
                "score": coco.score,
                "category_id": coco.category_id,
                "segmentation": coco.segmentation,
                "iscrowd": coco.iscrowd,
                "area": coco.area,
            }
            # Optionally include category_name (not used in COCO eval)
            # coco_dict["category_name"] = coco.category_name

            # Only add if bbox is valid (non-empty)
            if coco_dict["bbox"]:
                coco_predictions.append(coco_dict)
        except Exception as e:
            print(f"Failed to convert to COCO dict: {e}")
    return coco_predictions

In [6]:
# Function to get image details by image_id
def get_image_id(coco_data, image_name):
    for image in coco_data["images"]:
        file_name = Path(image['file_name']).stem
        if file_name == image_name:
            return image['id']
    return None

In [7]:
def predict_multilevel_fine_sliced_images(input_folder, dataset_json_path, detection_model, base_slice_size=512):
    name = "exp"
    save_dir = Path(increment_path(Path("sliced_predictions") / name, exist_ok=False))
    os.makedirs(save_dir, exist_ok=True)

    if dataset_json_path:
        with open(dataset_json_path, "r") as file:
            data = json.load(file)
        
    vis_params = {
        "bbox_thickness": 2,
        "text_size": 0.5,
        "text_thickness": 1,
        "hide_labels": False,
        "hide_conf": False,
        "format": "png"
    }

    image_files = [
        f for f in os.listdir(input_folder)
        if f.lower().endswith((".jpg", ".jpeg", ".png"))
    ]

    print(f"\nRunning fine slicing prediction on {len(image_files)} image(s)...")
    total_prediction_time = 0.0
    grand_total_predictions = 0
    all_coco_preds = []

    for filename in image_files:
        image_path = os.path.join(input_folder, filename)
        image_pil = Image.open(image_path).convert("RGB")
        image_np = np.array(image_pil)
        image_h, image_w = image_np.shape[:2]
        filename_wo_ext = Path(filename).stem
        total_prediction_count = 0
        print("*****************************************")
        print("File Name: ", filename_wo_ext)
        print("*****************************************")
        
        img_id = get_image_id(data, filename_wo_ext) if dataset_json_path else None
        all_object_predictions = []

        #Base prediction
        t0 = time.time()
        intial_prediction = get_prediction(image_path, detection_model)
        t_base = (time.time() - t0)
        print(f"Base pred time: {t_base * 1000:.2f} ms")
        total_prediction_time += t_base
        print(f"Total Based pred time: {total_prediction_time * 1000:.2f} ms")
        full_preds = intial_prediction.object_prediction_list
        full_object_density = len(full_preds)
        print("Full Image Object Density:", full_object_density)

        for pred in full_preds:
            all_object_predictions.append(pred)
            
        total_prediction_count += len(all_object_predictions)
    
        # Split image into 2x2 grid
        grid_h, grid_w = image_h // 2, image_w // 2

        for row in range(2):
            for col in range(2):
                x1, y1 = col * grid_w, row * grid_h
                x2, y2 = min(x1 + grid_w, image_w), min(y1 + grid_h, image_h)
                sub_img = image_pil.crop((x1, y1, x2, y2))
                print("Cropped Image Dimension:", x1, y1, x2, y2)

                time_start = time.time()
                base_pred = get_prediction(sub_img, detection_model)
                time_end = time.time() - time_start
                
                print("Initial Prediction time is: {:.2f} ms".format(time_end * 1000))

                coarse_preds = base_pred.object_prediction_list
                object_density = len(coarse_preds)
                print("Slice Object Density:", object_density)
                
                slice_params = get_slice_parameters(object_density, base_slice_size)
            
                iteration_time = time_end
                
                preds = coarse_preds.copy()
                
                if slice_params:
                    slice_width, slice_height, overlap_w, overlap_h = slice_params
                    print("********* Slice Parameters ***********")
                    print("Slice Width: ", slice_width)
                    print("Slice Height: ", slice_height)
                    print("Overlap Width Ratio: ", overlap_w)
                    print("Overlap Height Ratio: ", overlap_h)

                    time_start_slice = time.time()
                    sliced_pred = get_sliced_prediction(
                        sub_img,
                        detection_model,
                        slice_height=slice_height,
                        slice_width=slice_width,
                        overlap_height_ratio=overlap_h,
                        overlap_width_ratio=overlap_w,
                        postprocess_type="NMS",
                        postprocess_match_metric="IOU",
                        postprocess_match_threshold=0.3,
                        postprocess_min_area=16,
                        verbose=0
                    )
                    time_end_slice = time.time() - time_start_slice
                    print("Sliced Prediction time is: {:.2f} ms".format(time_end_slice * 1000))
                    
                    iteration_time += time_end_slice
                    fine_preds = sliced_pred.object_prediction_list
                    print("Pre Adaptive Slicing: ", len(preds))
                    preds.extend(fine_preds)
                    print("Post Adaptive Slicing: ", len(preds))
                else:
                    print("Prediction time is: {:.2f} ms".format(time_end * 1000))

                total_prediction_time += iteration_time
                
                #Offset bounding boxes back to original image space
                for pred in preds:
                    pred.bbox.minx += x1
                    pred.bbox.maxx += x1
                    pred.bbox.miny += y1
                    pred.bbox.maxy += y1
                    all_object_predictions.append(pred)
        
                total_prediction_count += len(preds)

        print("________________________________________________")

        print("Total Prediction Count (Crop+Slice): ", len(all_object_predictions))
        
        # Merge all predictions for image
        merged_preds = apply_nms(all_object_predictions, iou_threshold=0.5)
        
        #object_prediction_list = ObjectPredictionList(all_object_predictions)
        #merged_keep = truncated_nms_merge(object_prediction_list.totensor())
        #selected_object_predictions = object_prediction_list[merged_keep].tolist()
        #if not isinstance(selected_object_predictions, list):
        #    selected_object_predictions = [selected_object_predictions]
        
        # Convert merged predictions to COCO format
        if dataset_json_path:
            coco_preds = merged_preds_to_coco(merged_preds, img_id)
            all_coco_preds.extend(coco_preds)
            
        # Visualization
        visualize_object_predictions(
            image=np.ascontiguousarray(image_pil),
            object_prediction_list=merged_preds,
            rect_th=vis_params["bbox_thickness"],
            text_size=vis_params["text_size"],
            text_th=vis_params["text_thickness"],
            hide_labels=vis_params["hide_labels"],
            hide_conf=vis_params["hide_conf"],
            output_dir=save_dir,
            file_name=filename_wo_ext,
            export_format=vis_params["format"]
        )

        grand_total_predictions += total_prediction_count

    if dataset_json_path:
        save_path = str(save_dir / "result.json")
        save_json(all_coco_preds, save_path)
   
    print(f"\nCompleted {len(image_files)} images.")
    print("Total Prediction Count (Before NMS Merge): ", grand_total_predictions)
    print("Total Prediction Count (After Final NMS Merge): ", len(merged_preds))
    print("Total Prediction time for all images is: {:.2f} ms".format(total_prediction_time * 1000))
    print(f"Prediction results are successfully exported to {save_dir}")


In [18]:
def predict_multilevel_fine_sliced_single_image(image_path, dataset_json_path, detection_model, base_slice_size=512):
    name = "exp"
    save_dir = Path(increment_path(Path("sliced_predictions") / name, exist_ok=False))
    os.makedirs(save_dir, exist_ok=True)

    if dataset_json_path:
        with open(dataset_json_path, "r") as file:
            data = json.load(file)
        
    vis_params = {
        "bbox_thickness": 2,
        "text_size": 0.5,
        "text_thickness": 1,
        "hide_labels": False,
        "hide_conf": False,
        "format": "png"
    }

    print(f"\nRunning fine slicing prediction on single image...")
    total_prediction_time = 0.0
    grand_total_predictions = 0
    all_coco_preds = []
    
    image_pil = Image.open(image_path).convert("RGB")
    image_np = np.array(image_pil)
    image_h, image_w = image_np.shape[:2]
    filename_with_ext = os.path.basename(image_path)
    filename_wo_ext = Path(filename_with_ext).stem
    total_prediction_count = 0
    
    print("*****************************************")
    print("File Name: ", filename_with_ext)
    print("*****************************************")
    
    img_id = get_image_id(data, filename_wo_ext) if dataset_json_path else None
    all_object_predictions = []

    #Base prediction
    t0 = time.time()
    intial_prediction = get_prediction(image_path, detection_model)
    t_base = (time.time() - t0)
    print(f"Base pred time: {t_base * 1000:.2f} ms")
    total_prediction_time += t_base
    print(f"Total Based pred time: {total_prediction_time * 1000:.2f} ms")
    full_preds = intial_prediction.object_prediction_list
    full_object_density = len(full_preds)
    print("Full Image Object Density:", full_object_density)

    for pred in full_preds:
        all_object_predictions.append(pred)
        
    total_prediction_count += len(all_object_predictions)

    # Split image into 2x2 grid
    grid_h, grid_w = image_h // 2, image_w // 2

    for row in range(2):
        for col in range(2):
            x1, y1 = col * grid_w, row * grid_h
            x2, y2 = min(x1 + grid_w, image_w), min(y1 + grid_h, image_h)
            sub_img = image_pil.crop((x1, y1, x2, y2))
            print("Cropped Image Dimension:", x1, y1, x2, y2)

            time_start = time.time()
            base_pred = get_prediction(sub_img, detection_model)
            time_end = time.time() - time_start
            
            print("Initial Prediction time is: {:.2f} ms".format(time_end * 1000))

            coarse_preds = base_pred.object_prediction_list
            object_density = len(coarse_preds)
            print("Slice Object Density:", object_density)
            
            slice_params = get_slice_parameters(object_density, base_slice_size)
        
            iteration_time = time_end
            
            preds = coarse_preds.copy()
            
            if slice_params:
                slice_width, slice_height, overlap_w, overlap_h = slice_params
                print("********* Slice Parameters ***********")
                print("Slice Width: ", slice_width)
                print("Slice Height: ", slice_height)
                print("Overlap Width Ratio: ", overlap_w)
                print("Overlap Height Ratio: ", overlap_h)

                time_start_slice = time.time()
                sliced_pred = get_sliced_prediction(
                    sub_img,
                    detection_model,
                    slice_height=slice_height,
                    slice_width=slice_width,
                    overlap_height_ratio=overlap_h,
                    overlap_width_ratio=overlap_w,
                    postprocess_type="NMS",
                    postprocess_match_metric="IOU",
                    postprocess_match_threshold=0.3,
                    postprocess_min_area=16,
                    verbose=0
                )
                time_end_slice = time.time() - time_start_slice
                print("Sliced Prediction time is: {:.2f} ms".format(time_end_slice * 1000))
                
                iteration_time += time_end_slice
                fine_preds = sliced_pred.object_prediction_list
                print("Pre Adaptive Slicing: ", len(preds))
                preds.extend(fine_preds)
                print("Post Adaptive Slicing: ", len(preds))
            else:
                print("Prediction time is: {:.2f} ms".format(time_end * 1000))

            total_prediction_time += iteration_time
            
            #Offset bounding boxes back to original image space
            for pred in preds:
                #count +=1
                #print("Count: ", count)
                pred.bbox.minx += x1
                pred.bbox.maxx += x1
                pred.bbox.miny += y1
                pred.bbox.maxy += y1
                all_object_predictions.append(pred)
    
            total_prediction_count += len(preds)
            #print("Total Prediction Count (Inside): ", len(all_object_predictions))

    print("________________________________________________")

    print("Total Prediction Count (Crop+Slice): ", len(all_object_predictions))
    
    # Merge all predictions for image
    merged_preds = apply_nms(all_object_predictions, iou_threshold=0.5)
    
    # Convert merged predictions to COCO format
    if dataset_json_path:
        coco_preds = merged_preds_to_coco(merged_preds, img_id)
        all_coco_preds.extend(coco_preds)
        
    # Visualization
    prediction_result = visualize_object_predictions(
        image=np.ascontiguousarray(image_pil),
        object_prediction_list=merged_preds,
        rect_th=vis_params["bbox_thickness"],
        text_size=vis_params["text_size"],
        text_th=vis_params["text_thickness"],
        hide_labels=vis_params["hide_labels"],
        hide_conf=vis_params["hide_conf"],
        output_dir=save_dir,
        file_name=filename_wo_ext,
        export_format=vis_params["format"]
    )

    grand_total_predictions += total_prediction_count

    if dataset_json_path:
        save_path = str(save_dir / "result.json")
        save_json(all_coco_preds, save_path)
   
    print("Total Prediction Count (Before NMS Merge): ", grand_total_predictions)
    print("Total Prediction Count (After Final NMS Merge): ", len(merged_preds))
    print("Total Prediction time for all images is: {:.2f} ms".format(total_prediction_time * 1000))
    print(f"Prediction results are successfully exported to {save_dir}")
    return prediction_result['image']

#### **Mix of 500 images**

In [10]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
# Using Different IoU threshold
source_folder = './custom_utils/testdev_subsets/mix/v1/images'
json_path = "./custom_utils/annotations/subset_visdrone_test_data_500_mix_v1.json"
slice_size = 256

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=detection_model,
    base_slice_size=slice_size              
)


Running fine slicing prediction on 500 image(s)...
*****************************************
File Name:  0000320_00300_d_0000004
*****************************************
Base pred time: 653.15 ms
Total Based pred time: 653.15 ms
Full Image Object Density: 43
Cropped Image Dimension: 0 0 680 382
Initial Prediction time is: 21.71 ms
Slice Object Density: 23
********* Slice Parameters ***********
Slice Width:  256
Slice Height:  256
Overlap Width Ratio:  0.15
Overlap Height Ratio:  0.15
Sliced Boxes Count: 6
POST PROCESS:  NMS
Original Prediction Count 49
Final Bounding Box Count (NMS):  10
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  13
Final Bounding Box Count (NMS):  2
Final Bounding Box Count (NMS):  3
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  4
Sliced Prediction time is: 216.17 ms
Pre Adaptive Slicing:  23
Post Adaptive Slicing:  57
Cropped Image Dimension: 680 0 1360 382
Initial Prediction time is: 20.51 ms
Slice Object Density: 23


In [12]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './custom_utils/annotations/subset_visdrone_test_data_500_mix_v1.json' --result_json_path './sliced_predictions/exp592/result.json'

loading annotations into memory...
Done (t=0.09s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.01s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=8.77s).
Accumulating evaluation results...
DONE (t=0.17s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.135
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.232
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.137
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.147
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.343
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.441
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.073
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.199
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

In [11]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
# Using Different IoU threshold
source_folder = './custom_utils/testdev_subsets/mix/v1/images'
json_path = "./custom_utils/annotations/subset_visdrone_test_data_500_mix_v1.json"
slice_size = 256

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=detection_model,
    base_slice_size=slice_size              
)


Running fine slicing prediction on 500 image(s)...
*****************************************
File Name:  0000320_00300_d_0000004
*****************************************
Base pred time: 1569.51 ms
Total Based pred time: 1569.51 ms
Full Image Object Density: 43
Cropped Image Dimension: 0 0 680 382
Initial Prediction time is: 350.78 ms
Slice Object Density: 23
********* Slice Parameters ***********
Slice Width:  256
Slice Height:  256
Overlap Width Ratio:  0.15
Overlap Height Ratio:  0.15
Sliced Boxes Count: 6
POST PROCESS:  NMS
Original Prediction Count 49
Final Bounding Box Count (NMS):  10
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  13
Final Bounding Box Count (NMS):  2
Final Bounding Box Count (NMS):  3
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  4
Sliced Prediction time is: 1354.32 ms
Pre Adaptive Slicing:  23
Post Adaptive Slicing:  57
Cropped Image Dimension: 680 0 1360 382
Initial Prediction time is: 21.63 ms
Slice Object Density:

In [13]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './custom_utils/annotations/subset_visdrone_test_data_500_mix_v1.json' --result_json_path './sliced_predictions/exp593/result.json'

loading annotations into memory...
Done (t=0.09s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.01s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=8.78s).
Accumulating evaluation results...
DONE (t=0.17s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.135
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.232
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.137
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.147
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.343
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.441
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.073
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.199
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

In [14]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
# Using Different IoU threshold
source_folder = './custom_utils/testdev_subsets/mix/v1/images'
json_path = "./custom_utils/annotations/subset_visdrone_test_data_500_mix_v1.json"
slice_size = 128

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=detection_model,
    base_slice_size=slice_size              
)


Running fine slicing prediction on 500 image(s)...
*****************************************
File Name:  0000320_00300_d_0000004
*****************************************
Base pred time: 40.97 ms
Total Based pred time: 40.97 ms
Full Image Object Density: 43
Cropped Image Dimension: 0 0 680 382
Initial Prediction time is: 22.07 ms
Slice Object Density: 23
********* Slice Parameters ***********
Slice Width:  128
Slice Height:  128
Overlap Width Ratio:  0.15
Overlap Height Ratio:  0.15
Sliced Boxes Count: 28
POST PROCESS:  NMS
Original Prediction Count 41
Final Bounding Box Count (NMS):  7
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  17
Final Bounding Box Count (NMS):  2
Final Bounding Box Count (NMS):  4
Final Bounding Box Count (NMS):  5
Sliced Prediction time is: 4415.87 ms
Pre Adaptive Slicing:  23
Post Adaptive Slicing:  59
Cropped Image Dimension: 680 0 1360 382
Initial Prediction time is: 1765.91 ms
Slice Object Density: 23
********* Slice Parameters *******

In [15]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './custom_utils/annotations/subset_visdrone_test_data_500_mix_v1.json' --result_json_path './sliced_predictions/exp594/result.json'

loading annotations into memory...
Done (t=0.09s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.01s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=9.21s).
Accumulating evaluation results...
DONE (t=0.20s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.123
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.207
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.127
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.110
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.343
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.445
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.053
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.201
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

In [16]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
# Using Different IoU threshold
source_folder = './custom_utils/testdev_subsets/mix/v1/images'
json_path = "./custom_utils/annotations/subset_visdrone_test_data_500_mix_v1.json"
slice_size = 64

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=detection_model,
    base_slice_size=slice_size              
)


Running fine slicing prediction on 500 image(s)...
*****************************************
File Name:  0000320_00300_d_0000004
*****************************************
Base pred time: 294.88 ms
Total Based pred time: 294.88 ms
Full Image Object Density: 43
Cropped Image Dimension: 0 0 680 382
Initial Prediction time is: 2115.76 ms
Slice Object Density: 23
********* Slice Parameters ***********
Slice Width:  64
Slice Height:  64
Overlap Width Ratio:  0.15
Overlap Height Ratio:  0.15
Sliced Boxes Count: 91
POST PROCESS:  NMS
Original Prediction Count 38
Final Bounding Box Count (NMS):  7
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  24
Final Bounding Box Count (NMS):  2
Final Bounding Box Count (NMS):  1
Sliced Prediction time is: 6163.81 ms
Pre Adaptive Slicing:  23
Post Adaptive Slicing:  58
Cropped Image Dimension: 680 0 1360 382
Initial Prediction time is: 20.88 ms
Slice Object Density: 23
********* Slice Parameters ***********
Slice Width:  64
Slice Height:

In [17]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './custom_utils/annotations/subset_visdrone_test_data_500_mix_v1.json' --result_json_path './sliced_predictions/exp595/result.json'

loading annotations into memory...
Done (t=0.09s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.01s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=8.76s).
Accumulating evaluation results...
DONE (t=0.18s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.136
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.229
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.142
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.119
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.366
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.445
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.058
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.216
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

#### **Sparse Images**

In [45]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
# Using Different IoU threshold
source_folder = './custom_utils/testdev_subsets/sparse/v1/images'
json_path = "./custom_utils/annotations/subset_visdrone_test_data_50_sparse_v1.json"
slice_size = 256

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=detection_model,
    base_slice_size=slice_size              
)


Running fine slicing prediction on 50 image(s)...
*****************************************
File Name:  9999973_00000_d_0000054
*****************************************
Base pred time: 302.26 ms
Total Based pred time: 302.26 ms
Full Image Object Density: 14
Cropped Image Dimension: 0 0 958 539
Initial Prediction time is: 10.47 ms
Slice Object Density: 6
Prediction time is: 10.47 ms
Cropped Image Dimension: 958 0 1916 539
Initial Prediction time is: 9.90 ms
Slice Object Density: 7
Prediction time is: 9.90 ms
Cropped Image Dimension: 0 539 958 1078
Initial Prediction time is: 8.73 ms
Slice Object Density: 0
Prediction time is: 8.73 ms
Cropped Image Dimension: 958 539 1916 1078
Initial Prediction time is: 9.22 ms
Slice Object Density: 8
Prediction time is: 9.22 ms
________________________________________________
Total Prediction Count (Crop+Slice):  35
*****************************************
File Name:  9999986_00000_d_0000027
*****************************************
Base pred time: 

In [46]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './custom_utils/annotations/subset_visdrone_test_data_50_sparse_v1.json' --result_json_path './sliced_predictions/exp551/result.json'

loading annotations into memory...
Done (t=0.00s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=0.14s).
Accumulating evaluation results...
DONE (t=0.01s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.233
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.362
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.298
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.131
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.563
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.573
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.071
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.376
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

In [34]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
# Using Different IoU threshold
source_folder = './custom_utils/testdev_subsets/sparse/v1/images'
json_path = "./custom_utils/annotations/subset_visdrone_test_data_50_sparse_v1.json"
slice_size = 256

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=detection_model,
    base_slice_size=slice_size              
)


Running fine slicing prediction on 50 image(s)...
*****************************************
File Name 9999973_00000_d_0000054
Base pred time: 106.52 ms
Total Based pred time: 106.52 ms
Full Image Object Density: 14
Count:  1
Count:  2
Count:  3
Count:  4
Count:  5
Count:  6
Count:  7
Count:  8
Count:  9
Count:  10
Count:  11
Count:  12
Count:  13
Count:  14
Cropped Image: 0 0 958 539
Initial Prediction time is: 9.97 ms
Slice Object Density: 6
Prediction time is: 9.97 ms
Total CROP PREDICTION AFTER: 116.49 ms
Count:  15
Count:  16
Count:  17
Count:  18
Count:  19
Count:  20
Total Prediction Count (Inside):  20
Cropped Image: 958 0 1916 539
Initial Prediction time is: 9.59 ms
Slice Object Density: 7
Prediction time is: 9.59 ms
Total CROP PREDICTION AFTER: 126.07 ms
Count:  21
Count:  22
Count:  23
Count:  24
Count:  25
Count:  26
Count:  27
Total Prediction Count (Inside):  27
Cropped Image: 0 539 958 1078
Initial Prediction time is: 8.76 ms
Slice Object Density: 0
Prediction time is: 8

In [35]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './custom_utils/annotations/subset_visdrone_test_data_50_sparse_v1.json' --result_json_path './sliced_predictions/exp547/result.json'

loading annotations into memory...
Done (t=0.00s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=0.14s).
Accumulating evaluation results...
DONE (t=0.01s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.233
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.362
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.298
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.131
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.563
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.573
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.071
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.376
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

In [47]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
# Using Different IoU threshold
source_folder = './custom_utils/testdev_subsets/sparse/v1/images'
json_path = "./custom_utils/annotations/subset_visdrone_test_data_50_sparse_v1.json"
slice_size = 128

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=detection_model,
    base_slice_size=slice_size              
)


Running fine slicing prediction on 50 image(s)...
*****************************************
File Name:  9999973_00000_d_0000054
*****************************************
Base pred time: 46.20 ms
Total Based pred time: 46.20 ms
Full Image Object Density: 14
Cropped Image Dimension: 0 0 958 539
Initial Prediction time is: 10.32 ms
Slice Object Density: 6
Prediction time is: 10.32 ms
Cropped Image Dimension: 958 0 1916 539
Initial Prediction time is: 10.06 ms
Slice Object Density: 7
Prediction time is: 10.06 ms
Cropped Image Dimension: 0 539 958 1078
Initial Prediction time is: 8.80 ms
Slice Object Density: 0
Prediction time is: 8.80 ms
Cropped Image Dimension: 958 539 1916 1078
Initial Prediction time is: 9.22 ms
Slice Object Density: 8
Prediction time is: 9.22 ms
________________________________________________
Total Prediction Count (Crop+Slice):  35
*****************************************
File Name:  9999986_00000_d_0000027
*****************************************
Base pred time: 

In [48]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './custom_utils/annotations/subset_visdrone_test_data_50_sparse_v1.json' --result_json_path './sliced_predictions/exp552/result.json'

loading annotations into memory...
Done (t=0.00s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=0.15s).
Accumulating evaluation results...
DONE (t=0.01s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.231
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.360
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.295
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.127
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.592
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.575
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.068
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.395
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

In [49]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
# Using Different IoU threshold
source_folder = './custom_utils/testdev_subsets/sparse/v1/images'
json_path = "./custom_utils/annotations/subset_visdrone_test_data_50_sparse_v1.json"
slice_size = 64

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=detection_model,
    base_slice_size=slice_size              
)


Running fine slicing prediction on 50 image(s)...
*****************************************
File Name:  9999973_00000_d_0000054
*****************************************
Base pred time: 47.04 ms
Total Based pred time: 47.04 ms
Full Image Object Density: 14
Cropped Image Dimension: 0 0 958 539
Initial Prediction time is: 10.45 ms
Slice Object Density: 6
Prediction time is: 10.45 ms
Cropped Image Dimension: 958 0 1916 539
Initial Prediction time is: 10.09 ms
Slice Object Density: 7
Prediction time is: 10.09 ms
Cropped Image Dimension: 0 539 958 1078
Initial Prediction time is: 8.89 ms
Slice Object Density: 0
Prediction time is: 8.89 ms
Cropped Image Dimension: 958 539 1916 1078
Initial Prediction time is: 9.32 ms
Slice Object Density: 8
Prediction time is: 9.32 ms
________________________________________________
Total Prediction Count (Crop+Slice):  35
*****************************************
File Name:  9999986_00000_d_0000027
*****************************************
Base pred time: 

In [50]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './custom_utils/annotations/subset_visdrone_test_data_50_sparse_v1.json' --result_json_path './sliced_predictions/exp553/result.json'

loading annotations into memory...
Done (t=0.00s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=0.15s).
Accumulating evaluation results...
DONE (t=0.01s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.233
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.363
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.298
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.123
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.595
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.575
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.067
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.397
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

#### **Low Images**

In [11]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
# Using Different IoU threshold
source_folder = './custom_utils/testdev_subsets/low/v1/images'
json_path = "./custom_utils/annotations/subset_visdrone_test_data_50_low_v1.json"
slice_size = 256

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=detection_model,
    base_slice_size=slice_size              
)


Running fine slicing prediction on 50 image(s)...
*****************************************
File Name:  9999941_00000_d_0000013
*****************************************
Base pred time: 1530.52 ms
Total Based pred time: 1530.52 ms
Full Image Object Density: 8
Cropped Image Dimension: 0 0 700 394
Initial Prediction time is: 21.92 ms
Slice Object Density: 4
Prediction time is: 21.92 ms
Cropped Image Dimension: 700 0 1400 394
Initial Prediction time is: 20.83 ms
Slice Object Density: 4
Prediction time is: 20.83 ms
Cropped Image Dimension: 0 394 700 788
Initial Prediction time is: 20.57 ms
Slice Object Density: 5
Prediction time is: 20.57 ms
Cropped Image Dimension: 700 394 1400 788
Initial Prediction time is: 20.37 ms
Slice Object Density: 4
Prediction time is: 20.37 ms
________________________________________________
Total Prediction Count (Crop+Slice):  25
*****************************************
File Name:  9999963_00000_d_0000064
*****************************************
Base pred t

In [12]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './custom_utils/annotations/subset_visdrone_test_data_50_low_v1.json' --result_json_path './sliced_predictions/exp582/result.json'

loading annotations into memory...
Done (t=0.00s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=0.33s).
Accumulating evaluation results...
DONE (t=0.02s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.178
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.288
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.202
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.180
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.386
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.725
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.100
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.226
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

In [13]:
result_predict_nms = predict(source='./custom_utils/testdev_subsets/low/v1',
                         dataset_json_path = './custom_utils/annotations/subset_visdrone_test_data_50_low_v1.json',
                         model_type = 'ultralytics',
                         model_path = 'models/yolov8/last.pt',
                         slice_height = 128,
                         slice_width = 128,
                         overlap_height_ratio = 0.5,
                         overlap_width_ratio = 0.5,
                         postprocess_type = "NMS",
                         postprocess_min_area = 16,
                         postprocess_conf_threshold = 0.3,                  
                         verbose = 2
                        )

POST PROCESSING: NMS
indexing coco dataset annotations...


Performing inference on images:   0%|          | 0/50 [00:00<?, ?it/s]

Image Name: 9999941_00000_d_0000013
Image Size:  (1400, 788)
Sliced Boxes Count: 252
POST PROCESS:  NMS
Performing prediction on 252 slices.


Performing inference on images:   2%|▏         | 1/50 [00:06<05:39,  6.93s/it]

Original Prediction Count 334
Final Bounding Box Count (NMS):  13
Final Bounding Box Count (NMS):  88
Final Bounding Box Count (NMS):  10
Final Bounding Box Count (NMS):  4
Final Bounding Box Count (NMS):  10
Final Bounding Box Count (NMS):  10
Prediction time is: 6801.27 ms
Image Name: 9999963_00000_d_0000064
Image Size:  (1400, 1050)
Sliced Boxes Count: 336
POST PROCESS:  NMS
Performing prediction on 336 slices.


...

Original Prediction Count 225
Final Bounding Box Count (NMS):  28
Final Bounding Box Count (NMS):  3
Final Bounding Box Count (NMS):  48
Final Bounding Box Count (NMS):  19
Final Bounding Box Count (NMS):  7
Final Bounding Box Count (NMS):  12
Prediction time is: 10349.37 ms
Image Name: 9999938_00000_d_0000143
Image Size:  (1400, 788)
Sliced Boxes Count: 252
POST PROCESS:  NMS
Performing prediction on 252 slices.


Performing inference on images:  98%|█████████▊| 49/50 [06:02<00:07,  7.46s/it]

Original Prediction Count 240
Final Bounding Box Count (NMS):  25
Final Bounding Box Count (NMS):  55
Final Bounding Box Count (NMS):  4
Final Bounding Box Count (NMS):  7
Final Bounding Box Count (NMS):  15
Final Bounding Box Count (NMS):  1
Prediction time is: 5531.88 ms
Image Name: 9999976_00000_d_0000024
Image Size:  (1400, 788)
Sliced Boxes Count: 252
POST PROCESS:  NMS
Performing prediction on 252 slices.


Performing inference on images: 100%|██████████| 50/50 [06:07<00:00,  7.36s/it]

Original Prediction Count 91
Final Bounding Box Count (NMS):  9
Final Bounding Box Count (NMS):  19
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  2
Final Bounding Box Count (NMS):  2
Prediction time is: 5634.50 ms
Prediction results are successfully exported to runs/predict/exp324
Model loaded in 0.14044857025146484 seconds.
Slicing performed in 0.12002372741699219 seconds.
Prediction performed in 361.2484221458435 seconds.
Exporting performed in 0.045935869216918945 seconds.


In [14]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './custom_utils/annotations/subset_visdrone_test_data_50_low_v1.json' --result_json_path './runs/predict/exp324/result.json'

loading annotations into memory...
Done (t=0.00s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=0.56s).
Accumulating evaluation results...
DONE (t=0.03s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.103
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.168
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.100
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.096
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.284
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.676
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.049
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.160
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

In [15]:
result_predict_nms = predict(source='./custom_utils/testdev_subsets/low/v1',
                         dataset_json_path = './custom_utils/annotations/subset_visdrone_test_data_50_low_v1.json',
                         model_type = 'ultralytics',
                         model_path = 'models/yolov8/last.pt',
                         slice_height = 64,
                         slice_width = 64,
                         overlap_height_ratio = 0.5,
                         overlap_width_ratio = 0.5,
                         postprocess_type = "NMS",
                         postprocess_min_area = 16,
                         postprocess_conf_threshold = 0.3,                  
                         verbose = 2
                        )

POST PROCESSING: NMS
indexing coco dataset annotations...


Performing inference on images:   0%|          | 0/50 [00:00<?, ?it/s]

Image Name: 9999941_00000_d_0000013
Image Size:  (1400, 788)
Sliced Boxes Count: 1032
POST PROCESS:  NMS
Performing prediction on 1032 slices.


Performing inference on images:   2%|▏         | 1/50 [00:23<19:00, 23.29s/it]

Original Prediction Count 194
Final Bounding Box Count (NMS):  2
Final Bounding Box Count (NMS):  80
Final Bounding Box Count (NMS):  7
Final Bounding Box Count (NMS):  1
Prediction time is: 23159.39 ms
Image Name: 9999963_00000_d_0000064
Image Size:  (1400, 1050)
Sliced Boxes Count: 1376
POST PROCESS:  NMS
Performing prediction on 1376 slices.


...

Sliced Boxes Count: 1032
POST PROCESS:  NMS
Performing prediction on 1032 slices.


Performing inference on images:  98%|█████████▊| 49/50 [24:18<00:31, 31.82s/it]

Original Prediction Count 188
Final Bounding Box Count (NMS):  10
Final Bounding Box Count (NMS):  49
Final Bounding Box Count (NMS):  7
Final Bounding Box Count (NMS):  5
Final Bounding Box Count (NMS):  16
Final Bounding Box Count (NMS):  1
Prediction time is: 23120.23 ms
Image Name: 9999976_00000_d_0000024
Image Size:  (1400, 788)
Sliced Boxes Count: 1032
POST PROCESS:  NMS
Performing prediction on 1032 slices.


Performing inference on images: 100%|██████████| 50/50 [24:44<00:00, 29.70s/it]

Original Prediction Count 27
Final Bounding Box Count (NMS):  4
Final Bounding Box Count (NMS):  10
Final Bounding Box Count (NMS):  2
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  1
Prediction time is: 26011.11 ms
Prediction results are successfully exported to runs/predict/exp325
Model loaded in 0.028523921966552734 seconds.
Slicing performed in 0.6401445865631104 seconds.
Prediction performed in 1478.3492410182953 seconds.
Exporting performed in 0.04688382148742676 seconds.


In [16]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './custom_utils/annotations/subset_visdrone_test_data_50_low_v1.json' --result_json_path './runs/predict/exp325/result.json'

loading annotations into memory...
Done (t=0.00s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=0.50s).
Accumulating evaluation results...
DONE (t=0.03s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.113
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.183
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.112
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.041
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.325
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.689
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.019
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.187
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

In [11]:
result_predict_nms = predict(source='./custom_utils/testdev_subsets/low/v1',
                         dataset_json_path = './custom_utils/annotations/subset_visdrone_test_data_50_low_v1.json',
                         model_type = 'ultralytics',
                         model_path = 'models/yolov8/last.pt',
                         slice_height = 256,
                         slice_width = 256,
                         overlap_height_ratio = 0.5,
                         overlap_width_ratio = 0.5,
                         postprocess_type = "NMS",
                         postprocess_min_area = 16,
                         postprocess_conf_threshold = 0.3,                  
                         verbose = 2
                        )

POST PROCESSING: NMS
indexing coco dataset annotations...


Performing inference on images:   0%|          | 0/50 [00:00<?, ?it/s]

Image Name: 9999941_00000_d_0000013
Image Size:  (1400, 788)
Sliced Boxes Count: 60
POST PROCESS:  NMS
Performing prediction on 60 slices.


Performing inference on images:   2%|▏         | 1/50 [00:02<01:49,  2.23s/it]

Original Prediction Count 126
Final Bounding Box Count (NMS):  10
Final Bounding Box Count (NMS):  20
Final Bounding Box Count (NMS):  9
Final Bounding Box Count (NMS):  2
Final Bounding Box Count (NMS):  1
Prediction time is: 2112.91 ms
Image Name: 9999963_00000_d_0000064
Image Size:  (1400, 1050)
Sliced Boxes Count: 80
POST PROCESS:  NMS
Performing prediction on 80 slices.


...

Original Prediction Count 361
Final Bounding Box Count (NMS):  27
Final Bounding Box Count (NMS):  3
Final Bounding Box Count (NMS):  78
Final Bounding Box Count (NMS):  14
Final Bounding Box Count (NMS):  18
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  14
Prediction time is: 3177.93 ms
Image Name: 9999938_00000_d_0000143
Image Size:  (1400, 788)
Sliced Boxes Count: 60
POST PROCESS:  NMS
Performing prediction on 60 slices.


Performing inference on images:  98%|█████████▊| 49/50 [01:43<00:02,  2.29s/it]

Original Prediction Count 137
Final Bounding Box Count (NMS):  10
Final Bounding Box Count (NMS):  13
Final Bounding Box Count (NMS):  5
Final Bounding Box Count (NMS):  2
Final Bounding Box Count (NMS):  19
Prediction time is: 1573.00 ms
Image Name: 9999976_00000_d_0000024
Image Size:  (1400, 788)
Sliced Boxes Count: 60
POST PROCESS:  NMS
Performing prediction on 60 slices.


Performing inference on images: 100%|██████████| 50/50 [01:45<00:00,  2.11s/it]

Original Prediction Count 55
Final Bounding Box Count (NMS):  3
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  8
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  1
Prediction time is: 1659.36 ms
Prediction results are successfully exported to runs/predict/exp323
Model loaded in 0.030751705169677734 seconds.
Slicing performed in 0.07853531837463379 seconds.
Prediction performed in 99.39705467224121 seconds.
Exporting performed in 0.04598426818847656 seconds.


In [12]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './custom_utils/annotations/subset_visdrone_test_data_50_low_v1.json' --result_json_path './runs/predict/exp323/result.json'

loading annotations into memory...
Done (t=0.00s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=0.30s).
Accumulating evaluation results...
DONE (t=0.02s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.117
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.196
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.115
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.110
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.288
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.672
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.052
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.160
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

In [9]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
# Using Different IoU threshold
source_folder = './custom_utils/testdev_subsets/low/v1/images'
json_path = "./custom_utils/annotations/subset_visdrone_test_data_50_low_v1.json"
slice_size = 128

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=detection_model,
    base_slice_size=slice_size              
)


Running fine slicing prediction on 50 image(s)...
*****************************************
File Name:  9999941_00000_d_0000013
*****************************************
Base pred time: 805.49 ms
Total Based pred time: 805.49 ms
Full Image Object Density: 8
Cropped Image Dimension: 0 0 700 394
Initial Prediction time is: 22.07 ms
Slice Object Density: 4
Prediction time is: 22.07 ms
Cropped Image Dimension: 700 0 1400 394
Initial Prediction time is: 20.81 ms
Slice Object Density: 4
Prediction time is: 20.81 ms
Cropped Image Dimension: 0 394 700 788
Initial Prediction time is: 20.63 ms
Slice Object Density: 5
Prediction time is: 20.63 ms
Cropped Image Dimension: 700 394 1400 788
Initial Prediction time is: 20.62 ms
Slice Object Density: 4
Prediction time is: 20.62 ms
________________________________________________
Total Prediction Count (Crop+Slice):  25
*****************************************
File Name:  9999963_00000_d_0000064
*****************************************
Base pred tim

In [10]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './custom_utils/annotations/subset_visdrone_test_data_50_low_v1.json' --result_json_path './sliced_predictions/exp588/result.json'

loading annotations into memory...
Done (t=0.00s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=0.28s).
Accumulating evaluation results...
DONE (t=0.02s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.178
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.286
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.203
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.146
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.389
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.741
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.086
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.229
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

In [16]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
# Using Different IoU threshold
source_folder = './custom_utils/testdev_subsets/low/v1/images'
json_path = "./custom_utils/annotations/subset_visdrone_test_data_50_low_v1.json"
slice_size = 128

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=detection_model,
    base_slice_size=slice_size              
)


Running fine slicing prediction on 50 image(s)...
*****************************************
File Name:  9999941_00000_d_0000013
*****************************************
Base pred time: 48.18 ms
Total Based pred time: 48.18 ms
Full Image Object Density: 8
Cropped Image Dimension: 0 0 700 394
Initial Prediction time is: 21.97 ms
Slice Object Density: 4
Prediction time is: 21.97 ms
Cropped Image Dimension: 700 0 1400 394
Initial Prediction time is: 21.18 ms
Slice Object Density: 4
Prediction time is: 21.18 ms
Cropped Image Dimension: 0 394 700 788
Initial Prediction time is: 20.79 ms
Slice Object Density: 5
Prediction time is: 20.79 ms
Cropped Image Dimension: 700 394 1400 788
Initial Prediction time is: 20.68 ms
Slice Object Density: 4
Prediction time is: 20.68 ms
________________________________________________
Total Prediction Count (Crop+Slice):  25
*****************************************
File Name:  9999963_00000_d_0000064
*****************************************
Base pred time:

In [17]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './custom_utils/annotations/subset_visdrone_test_data_50_low_v1.json' --result_json_path './sliced_predictions/exp583/result.json'

loading annotations into memory...
Done (t=0.00s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=0.27s).
Accumulating evaluation results...
DONE (t=0.02s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.178
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.286
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.203
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.146
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.389
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.741
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.086
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.229
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

In [18]:
result_predict_nms = predict(source='./custom_utils/testdev_subsets/low/v1',
                         dataset_json_path = './custom_utils/annotations/subset_visdrone_test_data_50_low_v1.json',
                         model_type = 'ultralytics',
                         model_path = 'models/yolov8/last.pt',
                         slice_height = 128,
                         slice_width = 128,
                         overlap_height_ratio = 0.5,
                         overlap_width_ratio = 0.5,
                         postprocess_type = "NMS",
                         postprocess_min_area = 16,
                         postprocess_conf_threshold = 0.3,                  
                         verbose = 2
                        )

POST PROCESSING: NMS
indexing coco dataset annotations...


Performing inference on images:   0%|          | 0/50 [00:00<?, ?it/s]

Image Name: 9999941_00000_d_0000013
Image Size:  (1400, 788)
Sliced Boxes Count: 252
POST PROCESS:  NMS
Performing prediction on 252 slices.


Performing inference on images:   2%|▏         | 1/50 [00:06<05:19,  6.51s/it]

Original Prediction Count 334
Final Bounding Box Count (NMS):  13
Final Bounding Box Count (NMS):  88
Final Bounding Box Count (NMS):  10
Final Bounding Box Count (NMS):  4
Final Bounding Box Count (NMS):  10
Final Bounding Box Count (NMS):  10
Prediction time is: 6378.96 ms
Image Name: 9999963_00000_d_0000064
Image Size:  (1400, 1050)
Sliced Boxes Count: 336
POST PROCESS:  NMS
Performing prediction on 336 slices.


...

Original Prediction Count 225
Final Bounding Box Count (NMS):  28
Final Bounding Box Count (NMS):  3
Final Bounding Box Count (NMS):  48
Final Bounding Box Count (NMS):  19
Final Bounding Box Count (NMS):  7
Final Bounding Box Count (NMS):  12
Prediction time is: 12119.60 ms
Image Name: 9999938_00000_d_0000143
Image Size:  (1400, 788)
Sliced Boxes Count: 252
POST PROCESS:  NMS
Performing prediction on 252 slices.


Performing inference on images:  98%|█████████▊| 49/50 [06:05<00:08,  8.32s/it]

Original Prediction Count 240
Final Bounding Box Count (NMS):  25
Final Bounding Box Count (NMS):  55
Final Bounding Box Count (NMS):  4
Final Bounding Box Count (NMS):  7
Final Bounding Box Count (NMS):  15
Final Bounding Box Count (NMS):  1
Prediction time is: 6763.36 ms
Image Name: 9999976_00000_d_0000024
Image Size:  (1400, 788)
Sliced Boxes Count: 252
POST PROCESS:  NMS
Performing prediction on 252 slices.


Performing inference on images: 100%|██████████| 50/50 [06:12<00:00,  7.45s/it]

Original Prediction Count 91
Final Bounding Box Count (NMS):  9
Final Bounding Box Count (NMS):  19
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  2
Final Bounding Box Count (NMS):  2
Prediction time is: 6548.41 ms
Prediction results are successfully exported to runs/predict/exp321
Model loaded in 0.030156850814819336 seconds.
Slicing performed in 0.12172603607177734 seconds.
Prediction performed in 365.73366260528564 seconds.
Exporting performed in 0.04600667953491211 seconds.


In [21]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './custom_utils/annotations/subset_visdrone_test_data_50_low_v1.json' --result_json_path './runs/predict/exp321/result.json'

loading annotations into memory...
Done (t=0.00s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=0.56s).
Accumulating evaluation results...
DONE (t=0.03s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.103
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.168
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.100
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.096
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.284
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.676
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.049
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.160
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

In [22]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
# Using Different IoU threshold
source_folder = './custom_utils/testdev_subsets/low/v1/images'
json_path = "./custom_utils/annotations/subset_visdrone_test_data_50_low_v1.json"
slice_size = 64

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=detection_model,
    base_slice_size=slice_size              
)



Running fine slicing prediction on 50 image(s)...
*****************************************
File Name:  9999941_00000_d_0000013
*****************************************
Base pred time: 55.56 ms
Total Based pred time: 55.56 ms
Full Image Object Density: 8
Cropped Image Dimension: 0 0 700 394
Initial Prediction time is: 24.30 ms
Slice Object Density: 4
Prediction time is: 24.30 ms
Cropped Image Dimension: 700 0 1400 394
Initial Prediction time is: 21.92 ms
Slice Object Density: 4
Prediction time is: 21.92 ms
Cropped Image Dimension: 0 394 700 788
Initial Prediction time is: 21.66 ms
Slice Object Density: 5
Prediction time is: 21.66 ms
Cropped Image Dimension: 700 394 1400 788
Initial Prediction time is: 21.67 ms
Slice Object Density: 4
Prediction time is: 21.67 ms
________________________________________________
Total Prediction Count (Crop+Slice):  25
*****************************************
File Name:  9999963_00000_d_0000064
*****************************************
Base pred time:

In [23]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './custom_utils/annotations/subset_visdrone_test_data_50_low_v1.json' --result_json_path './sliced_predictions/exp584/result.json'

loading annotations into memory...
Done (t=0.00s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=0.27s).
Accumulating evaluation results...
DONE (t=0.02s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.180
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.289
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.207
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.138
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.394
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.741
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.084
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.232
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

In [24]:
result_predict_nms = predict(source='./custom_utils/testdev_subsets/low/v1',
                         dataset_json_path = './custom_utils/annotations/subset_visdrone_test_data_50_low_v1.json',
                         model_type = 'ultralytics',
                         model_path = 'models/yolov8/last.pt',
                         slice_height = 64,
                         slice_width = 64,
                         overlap_height_ratio = 0.5,
                         overlap_width_ratio = 0.5,
                         postprocess_type = "NMS",
                         postprocess_min_area = 16,
                         postprocess_conf_threshold = 0.3,                  
                         verbose = 2
                        )

POST PROCESSING: NMS
indexing coco dataset annotations...


Performing inference on images:   0%|          | 0/50 [00:00<?, ?it/s]

Image Name: 9999941_00000_d_0000013
Image Size:  (1400, 788)
Sliced Boxes Count: 1032
POST PROCESS:  NMS
Performing prediction on 1032 slices.


Performing inference on images:   2%|▏         | 1/50 [00:24<20:17, 24.86s/it]

Original Prediction Count 194
Final Bounding Box Count (NMS):  2
Final Bounding Box Count (NMS):  80
Final Bounding Box Count (NMS):  7
Final Bounding Box Count (NMS):  1
Prediction time is: 24732.93 ms
Image Name: 9999963_00000_d_0000064
Image Size:  (1400, 1050)
Sliced Boxes Count: 1376
POST PROCESS:  NMS
Performing prediction on 1376 slices.


...

Original Prediction Count 67
Final Bounding Box Count (NMS):  27
Final Bounding Box Count (NMS):  3
Final Bounding Box Count (NMS):  5
Final Bounding Box Count (NMS):  3
Final Bounding Box Count (NMS):  7
Prediction time is: 52058.88 ms
Image Name: 9999938_00000_d_0000143
Image Size:  (1400, 788)
Sliced Boxes Count: 1032
POST PROCESS:  NMS
Performing prediction on 1032 slices.


Performing inference on images:  98%|█████████▊| 49/50 [24:15<00:33, 33.49s/it]

Original Prediction Count 188
Final Bounding Box Count (NMS):  10
Final Bounding Box Count (NMS):  49
Final Bounding Box Count (NMS):  7
Final Bounding Box Count (NMS):  5
Final Bounding Box Count (NMS):  16
Final Bounding Box Count (NMS):  1
Prediction time is: 25519.92 ms
Image Name: 9999976_00000_d_0000024
Image Size:  (1400, 788)
Sliced Boxes Count: 1032
POST PROCESS:  NMS
Performing prediction on 1032 slices.


Performing inference on images: 100%|██████████| 50/50 [24:39<00:00, 29.59s/it]

Original Prediction Count 27
Final Bounding Box Count (NMS):  4
Final Bounding Box Count (NMS):  10
Final Bounding Box Count (NMS):  2
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  1
Prediction time is: 23728.04 ms
Prediction results are successfully exported to runs/predict/exp322
Model loaded in 0.03057265281677246 seconds.
Slicing performed in 0.5113973617553711 seconds.
Prediction performed in 1472.722557067871 seconds.
Exporting performed in 0.04609084129333496 seconds.


In [25]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './custom_utils/annotations/subset_visdrone_test_data_50_low_v1.json' --result_json_path './runs/predict/exp322/result.json'

loading annotations into memory...
Done (t=0.00s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=0.50s).
Accumulating evaluation results...
DONE (t=0.03s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.113
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.183
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.112
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.041
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.325
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.689
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.019
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.187
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

#### **Medium Images**

In [41]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
# Using Different IoU threshold
source_folder = './custom_utils/testdev_subsets/medium/v1/images'
json_path = "./custom_utils/annotations/subset_visdrone_test_data_50_medium_v1.json"
slice_size = 256

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=detection_model,
    base_slice_size=slice_size              
)


Running fine slicing prediction on 50 image(s)...
*****************************************
File Name 9999941_00000_d_0000004
Base pred time: 27.06 ms
Total Based pred time: 27.06 ms
Full Image Object Density: 28
Cropped Image Dimension: 0 0 700 394
Initial Prediction time is: 8.36 ms
Slice Object Density: 9
Prediction time is: 8.36 ms
Cropped Image Dimension: 700 0 1400 394
Initial Prediction time is: 7.41 ms
Slice Object Density: 0
Prediction time is: 7.41 ms
Cropped Image Dimension: 0 394 700 788
Initial Prediction time is: 7.84 ms
Slice Object Density: 15
********* Slice Parameters ***********
Slice Width:  256
Slice Height:  256
Overlap Width Ratio:  0.15
Overlap Height Ratio:  0.15
Sliced Boxes Count: 8
POST PROCESS:  NMS
Original Prediction Count 49
Final Bounding Box Count (NMS):  9
Final Bounding Box Count (NMS):  5
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  3
Sliced Prediction time is: 78.83 ms
Pre Adaptive Slicing:  15
Post Adaptive Slicing:  33
Cro

In [41]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
# Using Different IoU threshold
source_folder = './custom_utils/testdev_subsets/medium/v1/images'
json_path = "./custom_utils/annotations/subset_visdrone_test_data_50_medium_v1.json"
slice_size = 256

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=detection_model,
    base_slice_size=slice_size              
)


Running fine slicing prediction on 50 image(s)...
*****************************************
File Name 9999941_00000_d_0000004
Base pred time: 27.06 ms
Total Based pred time: 27.06 ms
Full Image Object Density: 28
Cropped Image Dimension: 0 0 700 394
Initial Prediction time is: 8.36 ms
Slice Object Density: 9
Prediction time is: 8.36 ms
Cropped Image Dimension: 700 0 1400 394
Initial Prediction time is: 7.41 ms
Slice Object Density: 0
Prediction time is: 7.41 ms
Cropped Image Dimension: 0 394 700 788
Initial Prediction time is: 7.84 ms
Slice Object Density: 15
********* Slice Parameters ***********
Slice Width:  256
Slice Height:  256
Overlap Width Ratio:  0.15
Overlap Height Ratio:  0.15
Sliced Boxes Count: 8
POST PROCESS:  NMS
Original Prediction Count 49
Final Bounding Box Count (NMS):  9
Final Bounding Box Count (NMS):  5
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  3
Sliced Prediction time is: 78.83 ms
Pre Adaptive Slicing:  15
Post Adaptive Slicing:  33
Cro

In [42]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './custom_utils/annotations/subset_visdrone_test_data_50_medium_v1.json' --result_json_path './sliced_predictions/exp550/result.json'

loading annotations into memory...
Done (t=0.00s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=0.48s).
Accumulating evaluation results...
DONE (t=0.02s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.133
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.239
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.132
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.166
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.394
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.673
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.079
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.237
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

In [36]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
# Using Different IoU threshold
source_folder = './custom_utils/testdev_subsets/dense/v1/images'
json_path = "./custom_utils/annotations/subset_visdrone_test_data_50_dense_v1.json"
slice_size = 256

# Run fine-sliced adaptive prediction
result = predict_fine_sliced_images_refactored_nms(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=detection_model,
    base_slice_size=slice_size              
)


Running fine slicing prediction on 50 image(s)...
*****************************************
File Name 9999979_00000_d_0000047
Cropped Image: 0 0 700 525
Initial Prediction time is: 12.46 ms
Object Density: 37
********* Slice Parameters ***********
Slice Width:  256
Slice Height:  256
Overlap Width Ratio:  0.25
Overlap Height Ratio:  0.25
Sliced Boxes Count: 12
POST PROCESS:  NMS
Original Prediction Count 151
Final Bounding Box Count (NMS):  3
Final Bounding Box Count (NMS):  45
Final Bounding Box Count (NMS):  8
Final Bounding Box Count (NMS):  2
Final Bounding Box Count (NMS):  1
Sliced Prediction time is: 121.91 ms
Pre Slicing:  37
Post Slicing:  96
Count: 1
Count: 2
Count: 3
Count: 4
Count: 5
Count: 6
Count: 7
Count: 8
Count: 9
Count: 10
Count: 11
Count: 12
Count: 13
Count: 14
Count: 15
Count: 16
Count: 17
Count: 18
Count: 19
Count: 20
Count: 21
Count: 22
Count: 23
Count: 24
Count: 25
Count: 26
Count: 27
Count: 28
Count: 29
Count: 30
Count: 31
Count: 32
Count: 33
Count: 34
Count: 3

In [37]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './custom_utils/annotations/subset_visdrone_test_data_50_dense_v1.json' --result_json_path './sliced_predictions/exp548/result.json'

loading annotations into memory...
Done (t=0.06s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=3.03s).
Accumulating evaluation results...
DONE (t=0.04s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.121
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.215
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.118
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.165
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.322
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.422
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.083
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.187
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

In [51]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
# Using Different IoU threshold
source_folder = './custom_utils/testdev_subsets/medium/v1/images'
json_path = "./custom_utils/annotations/subset_visdrone_test_data_50_medium_v1.json"
slice_size = 128

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=detection_model,
    base_slice_size=slice_size              
)


Running fine slicing prediction on 50 image(s)...
*****************************************
File Name:  9999941_00000_d_0000004
*****************************************
Base pred time: 29.38 ms
Total Based pred time: 29.38 ms
Full Image Object Density: 28
Cropped Image Dimension: 0 0 700 394
Initial Prediction time is: 8.44 ms
Slice Object Density: 9
Prediction time is: 8.44 ms
Cropped Image Dimension: 700 0 1400 394
Initial Prediction time is: 7.49 ms
Slice Object Density: 0
Prediction time is: 7.49 ms
Cropped Image Dimension: 0 394 700 788
Initial Prediction time is: 8.34 ms
Slice Object Density: 15
********* Slice Parameters ***********
Slice Width:  128
Slice Height:  128
Overlap Width Ratio:  0.15
Overlap Height Ratio:  0.15
Sliced Boxes Count: 28
POST PROCESS:  NMS
Original Prediction Count 39
Final Bounding Box Count (NMS):  21
Final Bounding Box Count (NMS):  5
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  3
Sliced Prediction time is: 191.73 ms
Pre Adapt

In [52]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './custom_utils/annotations/subset_visdrone_test_data_50_medium_v1.json' --result_json_path './sliced_predictions/exp554/result.json'

loading annotations into memory...
Done (t=0.00s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=0.57s).
Accumulating evaluation results...
DONE (t=0.02s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.120
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.214
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.123
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.138
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.397
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.673
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.066
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.240
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

In [53]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
# Using Different IoU threshold
source_folder = './custom_utils/testdev_subsets/medium/v1/images'
json_path = "./custom_utils/annotations/subset_visdrone_test_data_50_medium_v1.json"
slice_size = 64

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=detection_model,
    base_slice_size=slice_size              
)


Running fine slicing prediction on 50 image(s)...
*****************************************
File Name:  9999941_00000_d_0000004
*****************************************
Base pred time: 30.45 ms
Total Based pred time: 30.45 ms
Full Image Object Density: 28
Cropped Image Dimension: 0 0 700 394
Initial Prediction time is: 8.86 ms
Slice Object Density: 9
Prediction time is: 8.86 ms
Cropped Image Dimension: 700 0 1400 394
Initial Prediction time is: 7.57 ms
Slice Object Density: 0
Prediction time is: 7.57 ms
Cropped Image Dimension: 0 394 700 788
Initial Prediction time is: 7.80 ms
Slice Object Density: 15
********* Slice Parameters ***********
Slice Width:  64
Slice Height:  64
Overlap Width Ratio:  0.15
Overlap Height Ratio:  0.15
Sliced Boxes Count: 91
POST PROCESS:  NMS
Original Prediction Count 29
Final Bounding Box Count (NMS):  20
Final Bounding Box Count (NMS):  2
Final Bounding Box Count (NMS):  2
Final Bounding Box Count (NMS):  3
Sliced Prediction time is: 542.46 ms
Pre Adaptiv

In [54]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './custom_utils/annotations/subset_visdrone_test_data_50_medium_v1.json' --result_json_path './sliced_predictions/exp555/result.json'

loading annotations into memory...
Done (t=0.00s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=0.56s).
Accumulating evaluation results...
DONE (t=0.02s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.129
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.227
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.132
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.137
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.416
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.673
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.065
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.255
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

#### **Subset of 15 images (V5)**

In [35]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
source_folder = './test_subsets/v5/images'
json_path = "./subset_visdrone_test_data_15_v5.json"
slice_size = 256

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=detection_model,
    base_slice_size=slice_size              
)


Running fine slicing prediction on 15 image(s)...
*****************************************
File Name:  9999963_00000_d_0000057
*****************************************
Base pred time: 32.59 ms
Total Based pred time: 32.59 ms
Full Image Object Density: 33
Cropped Image Dimension: 0 0 700 525
Initial Prediction time is: 9.32 ms
Slice Object Density: 3
Prediction time is: 9.32 ms
Cropped Image Dimension: 700 0 1400 525
Initial Prediction time is: 9.12 ms
Slice Object Density: 20
********* Slice Parameters ***********
Slice Width:  256
Slice Height:  256
Overlap Width Ratio:  0.15
Overlap Height Ratio:  0.15
Sliced Boxes Count: 12
POST PROCESS:  NMS
Original Prediction Count 31
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  18
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  1
Sliced Prediction time is: 111.89 ms
Pre Adaptive Slicing:  20
Post Adaptive Slicing:  42
Cropped Image Dimension: 0 525 700 1050
Initial 

In [36]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './subset_visdrone_test_data_15_v5.json' --result_json_path './sliced_predictions/exp564/result.json'

loading annotations into memory...
Done (t=0.00s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=0.18s).
Accumulating evaluation results...
DONE (t=0.01s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.165
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.266
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.177
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.170
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.304
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.613
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.089
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.189
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

In [37]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
source_folder = './test_subsets/v5/images'
json_path = "./subset_visdrone_test_data_15_v5.json"
slice_size = 128

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=detection_model,
    base_slice_size=slice_size              
)


Running fine slicing prediction on 15 image(s)...
*****************************************
File Name:  9999963_00000_d_0000057
*****************************************
Base pred time: 36.58 ms
Total Based pred time: 36.58 ms
Full Image Object Density: 33
Cropped Image Dimension: 0 0 700 525
Initial Prediction time is: 9.84 ms
Slice Object Density: 3
Prediction time is: 9.84 ms
Cropped Image Dimension: 700 0 1400 525
Initial Prediction time is: 9.50 ms
Slice Object Density: 20
********* Slice Parameters ***********
Slice Width:  128
Slice Height:  128
Overlap Width Ratio:  0.15
Overlap Height Ratio:  0.15
Sliced Boxes Count: 35
POST PROCESS:  NMS
Original Prediction Count 38
Final Bounding Box Count (NMS):  25
Final Bounding Box Count (NMS):  6
Sliced Prediction time is: 240.83 ms
Pre Adaptive Slicing:  20
Post Adaptive Slicing:  51
Cropped Image Dimension: 0 525 700 1050
Initial Prediction time is: 8.56 ms
Slice Object Density: 7
Prediction time is: 8.56 ms
Cropped Image Dimension: 

In [38]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './subset_visdrone_test_data_15_v5.json' --result_json_path './sliced_predictions/exp565/result.json'

loading annotations into memory...
Done (t=0.00s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=0.20s).
Accumulating evaluation results...
DONE (t=0.01s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.165
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.259
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.177
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.142
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.337
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.613
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.073
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.211
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

In [39]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
source_folder = './test_subsets/v5/images'
json_path = "./subset_visdrone_test_data_15_v5.json"
slice_size = 64

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=detection_model,
    base_slice_size=slice_size              
)


Running fine slicing prediction on 15 image(s)...
*****************************************
File Name:  9999963_00000_d_0000057
*****************************************
Base pred time: 35.53 ms
Total Based pred time: 35.53 ms
Full Image Object Density: 33
Cropped Image Dimension: 0 0 700 525
Initial Prediction time is: 9.45 ms
Slice Object Density: 3
Prediction time is: 9.45 ms
Cropped Image Dimension: 700 0 1400 525
Initial Prediction time is: 9.43 ms
Slice Object Density: 20
********* Slice Parameters ***********
Slice Width:  64
Slice Height:  64
Overlap Width Ratio:  0.15
Overlap Height Ratio:  0.15
Sliced Boxes Count: 130
POST PROCESS:  NMS
Original Prediction Count 25
Final Bounding Box Count (NMS):  22
Final Bounding Box Count (NMS):  1
Sliced Prediction time is: 778.08 ms
Pre Adaptive Slicing:  20
Post Adaptive Slicing:  43
Cropped Image Dimension: 0 525 700 1050
Initial Prediction time is: 8.50 ms
Slice Object Density: 7
Prediction time is: 8.50 ms
Cropped Image Dimension: 7

In [40]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './subset_visdrone_test_data_15_v5.json' --result_json_path './sliced_predictions/exp566/result.json'

loading annotations into memory...
Done (t=0.00s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=0.19s).
Accumulating evaluation results...
DONE (t=0.01s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.174
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.276
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.184
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.150
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.346
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.613
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.079
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.216
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

#### **Subset of 50 images (V1)**

In [27]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
# Using Different IoU threshold
source_folder = './test_subsets/v6/images'
json_path = "./subset_visdrone_test_data_50_v1.json"
slice_size = 256

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=detection_model,
    base_slice_size=slice_size              
)


Running fine slicing prediction on 50 image(s)...
*****************************************
File Name:  9999938_00000_d_0000283
*****************************************
Base pred time: 87.99 ms
Total Based pred time: 87.99 ms
Full Image Object Density: 35
Cropped Image Dimension: 0 0 700 394
Initial Prediction time is: 7.90 ms
Slice Object Density: 18
********* Slice Parameters ***********
Slice Width:  256
Slice Height:  256
Overlap Width Ratio:  0.15
Overlap Height Ratio:  0.15
Sliced Boxes Count: 8
POST PROCESS:  NMS
Original Prediction Count 68
Final Bounding Box Count (NMS):  16
Final Bounding Box Count (NMS):  15
Final Bounding Box Count (NMS):  5
Final Bounding Box Count (NMS):  4
Sliced Prediction time is: 80.44 ms
Pre Adaptive Slicing:  18
Post Adaptive Slicing:  58
Cropped Image Dimension: 700 0 1400 394
Initial Prediction time is: 7.37 ms
Slice Object Density: 3
Prediction time is: 7.37 ms
Cropped Image Dimension: 0 394 700 788
Initial Prediction time is: 7.44 ms
Slice Obj

In [28]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './subset_visdrone_test_data_50_v1.json' --result_json_path './sliced_predictions/exp561/result.json'

loading annotations into memory...
Done (t=0.01s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=0.49s).
Accumulating evaluation results...
DONE (t=0.02s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.167
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.284
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.169
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.204
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.386
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.606
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.108
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.235
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

In [29]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
# Using Different IoU threshold
source_folder = './test_subsets/v6/images'
json_path = "./subset_visdrone_test_data_50_v1.json"
slice_size = 128

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=detection_model,
    base_slice_size=slice_size              
)


Running fine slicing prediction on 50 image(s)...
*****************************************
File Name:  9999938_00000_d_0000283
*****************************************
Base pred time: 29.74 ms
Total Based pred time: 29.74 ms
Full Image Object Density: 35
Cropped Image Dimension: 0 0 700 394
Initial Prediction time is: 8.55 ms
Slice Object Density: 18
********* Slice Parameters ***********
Slice Width:  128
Slice Height:  128
Overlap Width Ratio:  0.15
Overlap Height Ratio:  0.15
Sliced Boxes Count: 28
POST PROCESS:  NMS
Original Prediction Count 112
Final Bounding Box Count (NMS):  2
Final Bounding Box Count (NMS):  45
Final Bounding Box Count (NMS):  20
Final Bounding Box Count (NMS):  4
Final Bounding Box Count (NMS):  5
Final Bounding Box Count (NMS):  2
Sliced Prediction time is: 200.39 ms
Pre Adaptive Slicing:  18
Post Adaptive Slicing:  96
Cropped Image Dimension: 700 0 1400 394
Initial Prediction time is: 7.54 ms
Slice Object Density: 3
Prediction time is: 7.54 ms
Cropped Ima

In [30]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './subset_visdrone_test_data_50_v1.json' --result_json_path './sliced_predictions/exp562/result.json'

loading annotations into memory...
Done (t=0.00s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=0.57s).
Accumulating evaluation results...
DONE (t=0.02s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.158
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.264
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.162
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.170
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.397
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.606
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.087
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.247
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

In [31]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
# Using Different IoU threshold
source_folder = './test_subsets/v6/images'
json_path = "./subset_visdrone_test_data_50_v1.json"
slice_size = 64

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=detection_model,
    base_slice_size=slice_size              
)


Running fine slicing prediction on 50 image(s)...
*****************************************
File Name:  9999938_00000_d_0000283
*****************************************
Base pred time: 29.76 ms
Total Based pred time: 29.76 ms
Full Image Object Density: 35
Cropped Image Dimension: 0 0 700 394
Initial Prediction time is: 8.50 ms
Slice Object Density: 18
********* Slice Parameters ***********
Slice Width:  64
Slice Height:  64
Overlap Width Ratio:  0.15
Overlap Height Ratio:  0.15
Sliced Boxes Count: 91
POST PROCESS:  NMS
Original Prediction Count 70
Final Bounding Box Count (NMS):  51
Final Bounding Box Count (NMS):  8
Final Bounding Box Count (NMS):  4
Final Bounding Box Count (NMS):  2
Sliced Prediction time is: 542.22 ms
Pre Adaptive Slicing:  18
Post Adaptive Slicing:  83
Cropped Image Dimension: 700 0 1400 394
Initial Prediction time is: 7.57 ms
Slice Object Density: 3
Prediction time is: 7.57 ms
Cropped Image Dimension: 0 394 700 788
Initial Prediction time is: 7.67 ms
Slice Obje

In [32]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './subset_visdrone_test_data_50_v1.json' --result_json_path './sliced_predictions/exp563/result.json'

loading annotations into memory...
Done (t=0.01s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=0.57s).
Accumulating evaluation results...
DONE (t=0.02s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.176
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.288
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.183
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.178
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.410
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.606
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.092
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.259
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

#### **Single Images**

In [12]:
result_predict_nms = predict(source='./single_test',
                         dataset_json_path = './subset_visdrone_test_990.json',
                         model_type = 'ultralytics',
                         model_path = 'models/yolov8/last.pt',
                         slice_height = 256,
                         slice_width = 256,
                         overlap_height_ratio = 0.5,
                         overlap_width_ratio = 0.5,
                         postprocess_type = "NMS",
                         postprocess_min_area = 16,
                         postprocess_conf_threshold = 0.3,                  
                         verbose = 2,
                         no_sliced_prediction = True
                        )

POST PROCESSING: NMS
indexing coco dataset annotations...


Performing inference on images:   0%|          | 0/1 [00:00<?, ?it/s]

Image Name: 0000006_06773_d_0000018
Image Size:  (1360, 765)


Performing inference on images: 100%|██████████| 1/1 [00:00<00:00,  1.30it/s]

Prediction time is: 648.77 ms
Prediction results are successfully exported to runs/predict/exp326
Model loaded in 0.03131699562072754 seconds.
Slicing performed in 0 seconds.
Prediction performed in 0.6487741470336914 seconds.
Exporting performed in 0.04963541030883789 seconds.


In [13]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './subset_visdrone_test_990.json' --result_json_path './runs/predict/exp326/result.json'

loading annotations into memory...
Done (t=0.00s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=0.01s).
Accumulating evaluation results...
DONE (t=0.00s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.303
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.627
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.242
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.832
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.675
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.287
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.250
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.367
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

In [ ]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
source_folder = './single_test/images'
json_path = "./subset_visdrone_test_990.json"
slice_size = 256

# Run fine-sliced adaptive prediction
result = predict_fine_sliced_images_refactored_nms_1(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=detection_model,
    base_slice_size=slice_size              
)

In [39]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './subset_visdrone_test_990.json' --result_json_path './sliced_predictions/exp531/result.json'

loading annotations into memory...
Done (t=0.00s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=0.01s).
Accumulating evaluation results...
DONE (t=0.00s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.454
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.810
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.532
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.976
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.826
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.574
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.435
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.523
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

In [26]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
image_path = './single_test/images_v1/0000006_07596_d_0000020.jpg'
json_path = None #"./subset_visdrone_test_data_952.json"
slice_size = 256

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_single_image(
    image_path=image_path,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=detection_model,
    base_slice_size=slice_size              
)


Running fine slicing prediction on single image...
*****************************************
File Name:  0000006_07596_d_0000020.jpg
*****************************************
Base pred time: 40.40 ms
Total Based pred time: 40.40 ms
Full Image Object Density: 11
Cropped Image Dimension: 0 0 680 382
Initial Prediction time is: 22.47 ms
Slice Object Density: 5
Prediction time is: 22.47 ms
Cropped Image Dimension: 680 0 1360 382
Initial Prediction time is: 24.19 ms
Slice Object Density: 3
Prediction time is: 24.19 ms
Cropped Image Dimension: 0 382 680 764
Initial Prediction time is: 21.90 ms
Slice Object Density: 3
Prediction time is: 21.90 ms
Cropped Image Dimension: 680 382 1360 764
Initial Prediction time is: 21.59 ms
Slice Object Density: 1
Prediction time is: 21.59 ms
________________________________________________
Total Prediction Count (Crop+Slice):  23
Total Prediction Count (Before NMS Merge):  23
Total Prediction Count (After Final NMS Merge):  17
Total Prediction time for all 

In [25]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
image_path = './single_test/images_v1/0000006_07596_d_0000020.jpg'
json_path = "./subset_visdrone_test_data_952.json"
slice_size = 256

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_single_image(
    image_path=image_path,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=detection_model,
    base_slice_size=slice_size              
)


Running fine slicing prediction on single image...
*****************************************
File Name:  0000006_07596_d_0000020.jpg
*****************************************
Base pred time: 47.78 ms
Total Based pred time: 47.78 ms
Full Image Object Density: 11
Cropped Image Dimension: 0 0 680 382
Initial Prediction time is: 24.02 ms
Slice Object Density: 5
Prediction time is: 24.02 ms
Cropped Image Dimension: 680 0 1360 382
Initial Prediction time is: 21.27 ms
Slice Object Density: 3
Prediction time is: 21.27 ms
Cropped Image Dimension: 0 382 680 764
Initial Prediction time is: 21.51 ms
Slice Object Density: 3
Prediction time is: 21.51 ms
Cropped Image Dimension: 680 382 1360 764
Initial Prediction time is: 21.30 ms
Slice Object Density: 1
Prediction time is: 21.30 ms
________________________________________________
Total Prediction Count (Crop+Slice):  23
Total Prediction Count (Before NMS Merge):  23
Total Prediction Count (After Final NMS Merge):  17
Total Prediction time for all 

In [13]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
source_folder = './single_test/images_v1'
json_path = None #"./subset_visdrone_test_data_952.json"
slice_size = 256

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=detection_model,
    base_slice_size=slice_size              
)


Running fine slicing prediction on 1 image(s)...
*****************************************
File Name:  0000006_07596_d_0000020
*****************************************
Base pred time: 37.61 ms
Total Based pred time: 37.61 ms
Full Image Object Density: 11
Cropped Image Dimension: 0 0 680 382
Initial Prediction time is: 21.35 ms
Slice Object Density: 5
Prediction time is: 21.35 ms
Cropped Image Dimension: 680 0 1360 382
Initial Prediction time is: 30.12 ms
Slice Object Density: 3
Prediction time is: 30.12 ms
Cropped Image Dimension: 0 382 680 764
Initial Prediction time is: 31.02 ms
Slice Object Density: 3
Prediction time is: 31.02 ms
Cropped Image Dimension: 680 382 1360 764
Initial Prediction time is: 20.68 ms
Slice Object Density: 1
Prediction time is: 20.68 ms
________________________________________________
Total Prediction Count (Crop+Slice):  23

Completed 1 images.
Total Prediction Count (Before NMS Merge):  23
Total Prediction Count (After Final NMS Merge):  17
Total Predictio

In [9]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
source_folder = './single_test/images_v1'
json_path = "./subset_visdrone_test_data_952.json"
slice_size = 256

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=detection_model,
    base_slice_size=slice_size              
)


Running fine slicing prediction on 1 image(s)...
*****************************************
File Name:  0000006_07596_d_0000020
*****************************************
Base pred time: 878.96 ms
Total Based pred time: 878.96 ms
Full Image Object Density: 11
Cropped Image Dimension: 0 0 680 382
Initial Prediction time is: 22.22 ms
Slice Object Density: 5
Prediction time is: 22.22 ms
Cropped Image Dimension: 680 0 1360 382
Initial Prediction time is: 21.09 ms
Slice Object Density: 3
Prediction time is: 21.09 ms
Cropped Image Dimension: 0 382 680 764
Initial Prediction time is: 20.73 ms
Slice Object Density: 3
Prediction time is: 20.73 ms
Cropped Image Dimension: 680 382 1360 764
Initial Prediction time is: 20.70 ms
Slice Object Density: 1
Prediction time is: 20.70 ms
________________________________________________
Total Prediction Count (Crop+Slice):  23

Completed 1 images.
Total Prediction Count (Before NMS Merge):  23
Total Prediction Count (After Final NMS Merge):  17
Total Predict

In [10]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './subset_visdrone_test_data_952.json' --result_json_path './sliced_predictions/exp602/result.json'

loading annotations into memory...
Done (t=0.00s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=0.00s).
Accumulating evaluation results...
DONE (t=0.00s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.224
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.447
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.177
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.000
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.444
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 1.000
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.000
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.208
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

In [10]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
source_folder = './single_test/images'
json_path = "./subset_visdrone_test_990.json"
slice_size = 256

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=detection_model,
    base_slice_size=slice_size              
)


Running fine slicing prediction on 1 image(s)...
*****************************************
File Name:  0000006_06773_d_0000018
*****************************************
Base pred time: 37.68 ms
Total Based pred time: 37.68 ms
Full Image Object Density: 37
Cropped Image Dimension: 0 0 680 382
Initial Prediction time is: 20.86 ms
Slice Object Density: 15
********* Slice Parameters ***********
Slice Width:  256
Slice Height:  256
Overlap Width Ratio:  0.15
Overlap Height Ratio:  0.15
Sliced Boxes Count: 6
POST PROCESS:  NMS
Original Prediction Count 39
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  15
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  3
Final Bounding Box Count (NMS):  1
Sliced Prediction time is: 234.77 ms
Pre Adaptive Slicing:  15
Post Adaptive Slicing:  36
Cropped Image Dimension: 680 0 1360 382
Initial Prediction time is: 20.44 ms
Slice Object Density: 6
Prediction time is: 20.44 ms
Cropped Image Dimension: 0 382 680 764
Initial 

In [11]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './subset_visdrone_test_990.json' --result_json_path './sliced_predictions/exp590/result.json'

loading annotations into memory...
Done (t=0.00s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=0.01s).
Accumulating evaluation results...
DONE (t=0.00s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.454
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.810
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.532
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.976
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.826
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.574
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.435
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.523
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

In [14]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
source_folder = './single_test/images_bbk/images'
json_path = "./subset_vis_test_data_1563.json"
slice_size = 256

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=detection_model,
    base_slice_size=slice_size              
)


Running fine slicing prediction on 1 image(s)...
*****************************************
File Name 0000078_03171_d_0000009
Base pred time: 23.01 ms
Total Based pred time: 23.01 ms
Full Image Object Density: 55
Count:  1
Count:  2
Count:  3
Count:  4
Count:  5
Count:  6
Count:  7
Count:  8
Count:  9
Count:  10
Count:  11
Count:  12
Count:  13
Count:  14
Count:  15
Count:  16
Count:  17
Count:  18
Count:  19
Count:  20
Count:  21
Count:  22
Count:  23
Count:  24
Count:  25
Count:  26
Count:  27
Count:  28
Count:  29
Count:  30
Count:  31
Count:  32
Count:  33
Count:  34
Count:  35
Count:  36
Count:  37
Count:  38
Count:  39
Count:  40
Count:  41
Count:  42
Count:  43
Count:  44
Count:  45
Count:  46
Count:  47
Count:  48
Count:  49
Count:  50
Count:  51
Count:  52
Count:  53
Count:  54
Count:  55
Cropped Image: 0 0 680 382
Initial Prediction time is: 8.22 ms
********* Slice Parameters ***********
Slice Width:  256
Slice Height:  256
Overlap Width Ratio:  0.25
Overlap Height Ratio:  0.

In [46]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
source_folder = './single_test/images_bbk/images'
json_path = "./subset_vis_test_data_1563.json"
slice_size = 256

# Run fine-sliced adaptive prediction
result = predict_fine_sliced_images_refactored_nms_1(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=detection_model,
    base_slice_size=slice_size              
)


Running fine slicing prediction on 1 image(s)...
*****************************************
File Name 0000078_03171_d_0000009
Base pred time: 23.48 ms
Full Image Object Density: 55
Count:  1
Count:  2
Count:  3
Count:  4
Count:  5
Count:  6
Count:  7
Count:  8
Count:  9
Count:  10
Count:  11
Count:  12
Count:  13
Count:  14
Count:  15
Count:  16
Count:  17
Count:  18
Count:  19
Count:  20
Count:  21
Count:  22
Count:  23
Count:  24
Count:  25
Count:  26
Count:  27
Count:  28
Count:  29
Count:  30
Count:  31
Count:  32
Count:  33
Count:  34
Count:  35
Count:  36
Count:  37
Count:  38
Count:  39
Count:  40
Count:  41
Count:  42
Count:  43
Count:  44
Count:  45
Count:  46
Count:  47
Count:  48
Count:  49
Count:  50
Count:  51
Count:  52
Count:  53
Count:  54
Count:  55
Cropped Image: 0 0 680 382
Initial Prediction time is: 8.29 ms
Grid Slice Object Density (Before): 25
Grid Slice Object Density (After): 25
********* Slice Parameters ***********
Slice Width:  256
Slice Height:  256
Overlap

In [34]:
result_predict_nms = predict(source='./single_test/images_bbk',
                         dataset_json_path = './subset_vis_test_data_1563.json',
                         model_type = 'ultralytics',
                         model_path = 'models/yolov8/last.pt',
                         slice_height = 256,
                         slice_width = 256,
                         overlap_height_ratio = 0.5,
                         overlap_width_ratio = 0.5,
                         postprocess_type = "NMS",
                         postprocess_min_area = 16,
                         postprocess_conf_threshold = 0.3,                  
                         verbose = 2
                        )

POST PROCESSING: NMS
indexing coco dataset annotations...


Performing inference on images:   0%|          | 0/1 [00:00<?, ?it/s]

Image Name: 0000078_03171_d_0000009
Image Size:  (1360, 765)
Sliced Boxes Count: 50
POST PROCESS:  NMS
Performing prediction on 50 slices.


Performing inference on images: 100%|██████████| 1/1 [00:00<00:00,  1.58it/s]

Original Prediction Count 311
Final Bounding Box Count (NMS):  19
Final Bounding Box Count (NMS):  2
Final Bounding Box Count (NMS):  22
Final Bounding Box Count (NMS):  3
Final Bounding Box Count (NMS):  43
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  2
Prediction time is: 516.29 ms
Prediction results are successfully exported to runs/predict/exp308
Model loaded in 0.03419971466064453 seconds.
Slicing performed in 0.001177072525024414 seconds.
Prediction performed in 0.516291618347168 seconds.
Exporting performed in 0.04840564727783203 seconds.


In [41]:
result_predict_nms = predict(source='./single_test/images_bbk',
                         dataset_json_path = './subset_vis_test_data_1563.json',
                         model_type = 'ultralytics',
                         model_path = 'models/yolov8/last.pt',
                         slice_height = 128,
                         slice_width = 128,
                         overlap_height_ratio = 0.5,
                         overlap_width_ratio = 0.5,
                         postprocess_type = "NMS",
                         postprocess_min_area = 16,
                         postprocess_conf_threshold = 0.3,                  
                         verbose = 2
                        )

POST PROCESSING: NMS
indexing coco dataset annotations...


Performing inference on images:   0%|          | 0/1 [00:00<?, ?it/s]

Image Name: 0000078_03171_d_0000009
Image Size:  (1360, 765)
Sliced Boxes Count: 231
POST PROCESS:  NMS
Performing prediction on 231 slices.


Performing inference on images: 100%|██████████| 1/1 [00:01<00:00,  1.71s/it]

Original Prediction Count 228
Final Bounding Box Count (NMS):  16
Final Bounding Box Count (NMS):  50
Final Bounding Box Count (NMS):  5
Final Bounding Box Count (NMS):  38
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  7
Prediction time is: 1590.57 ms
Prediction results are successfully exported to runs/predict/exp309
Model loaded in 0.03683280944824219 seconds.
Slicing performed in 0.001980304718017578 seconds.
Prediction performed in 1.5905699729919434 seconds.
Exporting performed in 0.04936051368713379 seconds.


In [42]:
result_predict_nms = predict(source='./single_test/images_bbk',
                         dataset_json_path = './subset_vis_test_data_1563.json',
                         model_type = 'ultralytics',
                         model_path = 'models/yolov8/last.pt',
                         slice_height = 64,
                         slice_width = 64,
                         overlap_height_ratio = 0.5,
                         overlap_width_ratio = 0.5,
                         postprocess_type = "NMS",
                         postprocess_min_area = 16,
                         postprocess_conf_threshold = 0.3,                  
                         verbose = 2
                        )

POST PROCESSING: NMS
indexing coco dataset annotations...


Performing inference on images:   0%|          | 0/1 [00:00<?, ?it/s]

Image Name: 0000078_03171_d_0000009
Image Size:  (1360, 765)
Sliced Boxes Count: 966
POST PROCESS:  NMS
Performing prediction on 966 slices.


Performing inference on images: 100%|██████████| 1/1 [00:05<00:00,  5.91s/it]

Original Prediction Count 94
Final Bounding Box Count (NMS):  9
Final Bounding Box Count (NMS):  13
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  36
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  4
Prediction time is: 5800.93 ms
Prediction results are successfully exported to runs/predict/exp310
Model loaded in 0.04542279243469238 seconds.
Slicing performed in 0.004753828048706055 seconds.
Prediction performed in 5.8009257316589355 seconds.
Exporting performed in 0.0464785099029541 seconds.


In [98]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
source_folder = './test_subsets/v5/images'
json_path = "./subset_visdrone_test_data_15_v5.json"
slice_size = 256

# Run fine-sliced adaptive prediction
result = predict_fine_sliced_images_refactored_nms_1(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=detection_model,
    base_slice_size=slice_size              
)


Running fine slicing prediction on 15 image(s)...
*****************************************
File Name 9999963_00000_d_0000057
Base pred time: 35.07 ms
Full Image Object Density: 33
Cropped Image: 0 0 700 525
Initial Prediction time is: 8.89 ms
Grid Slice Object Density (Before): 3
Grid Slice Object Density (After): 36
Prediction time is: 8.89 ms
Cropped Image: 700 0 1400 525
Initial Prediction time is: 8.65 ms
Grid Slice Object Density (Before): 20
Grid Slice Object Density (After): 56
********* Slice Parameters ***********
Slice Width:  256
Slice Height:  256
Overlap Width Ratio:  0.15
Overlap Height Ratio:  0.15
Sliced Boxes Count: 12
POST PROCESS:  NMS
Original Prediction Count 31
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  18
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  1
Sliced Prediction time is: 107.45 ms
Pre Adaptive Slicing:  56
Post Adaptive Slicing:  78
Cropped Image: 0 525 700 1050
Initial Pr

In [15]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './subset_vis_test_data_1563.json' --result_json_path './sliced_predictions/exp544/result.json'

loading annotations into memory...
Done (t=0.00s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=0.03s).
Accumulating evaluation results...
DONE (t=0.01s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.225
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.412
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.255
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.234
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.671
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 1.000
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.092
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.331
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

In [10]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
source_folder = './single_test/images'
json_path = "./subset_visdrone_test_990.json"
slice_size = 256

# Run fine-sliced adaptive prediction
result = predict_fine_sliced_images_refactored_nms_1(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=detection_model,
    base_slice_size=slice_size              
)


Running fine slicing prediction on 1 image(s)...
*****************************************
File Name 0000006_06773_d_0000018
Base pred time: 1651.92 ms
Full Image Object Density: 37
Copy Intial Pred:  37
Cropped Image: 0 0 680 382
Initial Prediction time is: 8.45 ms
Grid Slice Object Density (Before): 15
Grid Slice Object Density (After): 52
********* Slice Parameters ***********
Slice Width:  256
Slice Height:  256
Overlap Width Ratio:  0.15
Overlap Height Ratio:  0.15
Sliced Boxes Count: 6
POST PROCESS:  NMS
Original Prediction Count 39
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  15
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  3
Final Bounding Box Count (NMS):  1
Sliced Prediction time is: 60.64 ms
Pre Adaptive Slicing:  52
Post Adaptive Slicing:  73
Total Prediction Count (First):  73
Count:  1
Count:  2
Count:  3
Count:  4
Count:  5
Count:  6
Count:  7
Count:  8
Count:  9
Count:  10
Count:  11
Count:  12
Count:  13
Count:  14
Count:  

In [99]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './subset_visdrone_test_data_15_v5.json' --result_json_path './sliced_predictions/exp508/result.json'

loading annotations into memory...
Done (t=0.00s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=0.23s).
Accumulating evaluation results...
DONE (t=0.01s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.012
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.022
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.012
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.030
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.041
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.002
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.018
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.025
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

In [20]:
# Run fine-sliced adaptive prediction
result = predict_fine_sliced_images_refactored_nms_1(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=detection_model,
    base_slice_size=slice_size              
)


Running fine slicing prediction on 1 image(s)...
*****************************************
File Name 0000006_06773_d_0000018
Base pred time: 25.05 ms
Full Image Object Density: 37
Cropped Image: 0 0 680 382
Initial Prediction time is: 8.04 ms
Grid Slice Object Density (Before): 15
Grid Slice Object Density (After): 52
********* Slice Parameters ***********
Slice Width:  256
Slice Height:  256
Overlap Width Ratio:  0.15
Overlap Height Ratio:  0.15
Sliced Boxes Count: 6
POST PROCESS:  NMS
Original Prediction Count 39
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  15
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  3
Final Bounding Box Count (NMS):  1
Sliced Prediction time is: 61.38 ms
Pre Adaptive Slicing:  52
Post Adaptive Slicing:  73
Cropped Image: 680 0 1360 382
Initial Prediction time is: 7.34 ms
Grid Slice Object Density (Before): 6
Grid Slice Object Density (After): 79
Prediction time is: 7.34 ms
Cropped Image: 0 382 680 764
Initial Predic

In [36]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './subset_visdrone_test_990.json' --result_json_path './sliced_predictions/exp520/result.json'

loading annotations into memory...
Done (t=0.00s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=0.01s).
Accumulating evaluation results...
DONE (t=0.00s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.429
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.772
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.493
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.976
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.770
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.574
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.435
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.488
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

In [14]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
source_folder = './single_test/images'
json_path = "./subset_visdrone_test_990.json"
slice_size = 256

# Run fine-sliced adaptive prediction
result = predict_fine_sliced_images_refactored_nms_1(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=detection_model,
    base_slice_size=slice_size              
)


Running fine slicing prediction on 1 image(s)...
*****************************************
File Name 0000006_06773_d_0000018
Base pred time: 23.44 ms
Full Image Object Density: 37
Cropped Image: 0 0 680 382
Initial Prediction time is: 7.86 ms
Grid Slice Object Density (Before): 15
Grid Slice Object Density (After): 52
********* Slice Parameters ***********
Slice Width:  256
Slice Height:  256
Overlap Width Ratio:  0.15
Overlap Height Ratio:  0.15
Sliced Boxes Count: 6
POST PROCESS:  NMS
Original Prediction Count 39
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  15
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  3
Final Bounding Box Count (NMS):  1
Sliced Prediction time is: 60.74 ms
Pre Adaptive Slicing:  52
Post Adaptive Slicing:  73
Cropped Image: 680 0 1360 382
Initial Prediction time is: 7.32 ms
Grid Slice Object Density (Before): 6
Grid Slice Object Density (After): 79
Prediction time is: 7.32 ms
Cropped Image: 0 382 680 764
Initial Predic

In [27]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
source_folder = './single_test/images'
json_path = "./subset_visdrone_test_990.json"
slice_size = 256

# Run fine-sliced adaptive prediction
result = predict_fine_sliced_images_refactored_nms_1(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=detection_model,
    base_slice_size=slice_size              
)


Running fine slicing prediction on 1 image(s)...
*****************************************
File Name 0000006_06773_d_0000018
Base pred time: 23.51 ms
Full Image Object Density: 37
Copy Intial Pred:  37
Cropped Image: 0 0 680 382
Initial Prediction time is: 7.83 ms
Grid Slice Object Density (Before): 15
Grid Slice Object Density (After): 52
********* Slice Parameters ***********
Slice Width:  256
Slice Height:  256
Overlap Width Ratio:  0.15
Overlap Height Ratio:  0.15
Sliced Boxes Count: 6
POST PROCESS:  NMS
Original Prediction Count 39
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  15
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  3
Final Bounding Box Count (NMS):  1
Sliced Prediction time is: 59.76 ms
Pre Adaptive Slicing:  52
Post Adaptive Slicing:  73
Total Prediction Count (First):  73
Cropped Image: 680 0 1360 382
Initial Prediction time is: 7.12 ms
Grid Slice Object Density (Before): 6
Grid Slice Object Density (After): 79
Prediction ti

In [29]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './subset_visdrone_test_990.json' --result_json_path './sliced_predictions/exp517/result.json'

loading annotations into memory...
Done (t=0.00s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=0.01s).
Accumulating evaluation results...
DONE (t=0.00s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.024
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.042
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.032
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.000
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.076
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.000
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.000
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.042
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

#### **Original Prediction Without Slicing**

In [4]:
result_predict_nms = predict(source='./test_subsets/v6',
                         dataset_json_path = './subset_visdrone_test_data_50_v1.json',
                         model_type = 'ultralytics',
                         model_path = 'models/yolov8/last.pt',
                         slice_height = 256,
                         slice_width = 256,
                         overlap_height_ratio = 0.5,
                         overlap_width_ratio = 0.5,
                         postprocess_type = "NMS",
                         postprocess_min_area = 16,
                         postprocess_conf_threshold = 0.3,                  
                         verbose = 2,
                         no_sliced_prediction = True
                        )

POST PROCESSING: NMS
indexing coco dataset annotations...


Performing inference on images:   0%|          | 0/50 [00:00<?, ?it/s]

Image Name: 9999938_00000_d_0000283
Image Size:  (1400, 788)


Performing inference on images:   2%|▏         | 1/50 [00:01<01:25,  1.75s/it]

Prediction time is: 1610.23 ms
Image Name: 9999938_00000_d_0000109
Image Size:  (1400, 788)
Prediction time is: 14.04 ms


...

Image Name: 9999938_00000_d_0000286
Image Size:  (1400, 788)
Prediction time is: 13.88 ms
Image Name: 9999952_00000_d_0000235
Image Size:  (1400, 788)
Prediction time is: 13.13 ms


Performing inference on images:  96%|█████████▌| 48/50 [00:08<00:00,  7.84it/s]

Image Name: 9999938_00000_d_0000323
Image Size:  (1400, 788)
Prediction time is: 13.18 ms
Image Name: 0000365_01500_d_0000226
Image Size:  (960, 540)
Prediction time is: 9.78 ms
Image Name: 9999973_00000_d_0000094
Image Size:  (1916, 1078)


Performing inference on images: 100%|██████████| 50/50 [00:08<00:00,  5.93it/s]


Prediction time is: 19.23 ms
Prediction results are successfully exported to runs/predict/exp316
Model loaded in 3.7892978191375732 seconds.
Slicing performed in 0 seconds.
Prediction performed in 2.388852119445801 seconds.
Exporting performed in 0.09826183319091797 seconds.


In [5]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './subset_visdrone_test_data_50_v1.json' --result_json_path './runs/predict/exp316/result.json'

loading annotations into memory...
Done (t=0.00s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=0.31s).
Accumulating evaluation results...
DONE (t=0.02s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.154
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.244
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.158
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.117
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.388
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.617
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.054
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.244
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

In [6]:
result_predict_nms = predict(source='./test_subsets/v6',
                         dataset_json_path = './subset_visdrone_test_data_50_v1.json',
                         model_type = 'ultralytics',
                         model_path = 'models/yolov8/last.pt',
                         slice_height = 128,
                         slice_width = 128,
                         overlap_height_ratio = 0.5,
                         overlap_width_ratio = 0.5,
                         postprocess_type = "NMS",
                         postprocess_min_area = 16,
                         postprocess_conf_threshold = 0.3,                  
                         verbose = 2,
                         no_sliced_prediction = True
                        )

POST PROCESSING: NMS
indexing coco dataset annotations...


Performing inference on images:   2%|▏         | 1/50 [00:00<00:09,  5.09it/s]

Image Name: 9999938_00000_d_0000283
Image Size:  (1400, 788)
Prediction time is: 71.35 ms
Image Name: 9999938_00000_d_0000109
Image Size:  (1400, 788)


Performing inference on images:   4%|▍         | 2/50 [00:00<00:07,  6.36it/s]

Prediction time is: 13.26 ms
Image Name: 9999986_00000_d_0000020
Image Size:  (1400, 1050)
Prediction time is: 17.14 ms


...

Image Name: 9999938_00000_d_0000286
Image Size:  (1400, 788)
Prediction time is: 14.01 ms
Image Name: 9999952_00000_d_0000235
Image Size:  (1400, 788)
Prediction time is: 13.71 ms


Performing inference on images:  96%|█████████▌| 48/50 [00:06<00:00,  7.82it/s]

Image Name: 9999938_00000_d_0000323
Image Size:  (1400, 788)
Prediction time is: 13.36 ms
Image Name: 0000365_01500_d_0000226
Image Size:  (960, 540)
Prediction time is: 9.75 ms
Image Name: 9999973_00000_d_0000094
Image Size:  (1916, 1078)


Performing inference on images: 100%|██████████| 50/50 [00:06<00:00,  7.33it/s]


Prediction time is: 19.40 ms
Prediction results are successfully exported to runs/predict/exp317
Model loaded in 0.04777884483337402 seconds.
Slicing performed in 0 seconds.
Prediction performed in 0.7861363887786865 seconds.
Exporting performed in 0.09587407112121582 seconds.


In [8]:
result_predict_nms = predict(source='./custom_utils/testdev_subsets/medium/v1',
                         dataset_json_path = './custom_utils/annotations/subset_visdrone_test_data_50_medium_v1.json',
                         model_type = 'ultralytics',
                         model_path = 'models/yolov8/last.pt',
                         postprocess_type = "NMS",
                         postprocess_min_area = 16,
                         postprocess_conf_threshold = 0.3,                  
                         verbose = 2,
                         no_sliced_prediction = True
                        )

POST PROCESSING: NMS
indexing coco dataset annotations...


Performing inference on images:   2%|▏         | 1/50 [00:00<00:09,  5.22it/s]

Image Name: 9999941_00000_d_0000004
Image Size:  (1400, 788)
Prediction time is: 73.18 ms
Image Name: 9999938_00000_d_0000009
Image Size:  (1400, 788)


Performing inference on images:   4%|▍         | 2/50 [00:00<00:07,  6.47it/s]

Prediction time is: 13.42 ms
Image Name: 9999986_00000_d_0000012
Image Size:  (1400, 1050)
Prediction time is: 16.60 ms


...

Image Name: 9999963_00000_d_0000018
Image Size:  (1400, 1050)
Prediction time is: 16.53 ms
Image Name: 9999952_00000_d_0000081
Image Size:  (1400, 788)
Prediction time is: 13.94 ms


Performing inference on images:  98%|█████████▊| 49/50 [00:06<00:00,  7.63it/s]

Image Name: 9999938_00000_d_0000323
Image Size:  (1400, 788)
Prediction time is: 13.59 ms
Image Name: 9999952_00000_d_0000062
Image Size:  (1400, 788)
Prediction time is: 13.34 ms


Performing inference on images: 100%|██████████| 50/50 [00:06<00:00,  7.36it/s]

Prediction results are successfully exported to runs/predict/exp318
Model loaded in 0.18895506858825684 seconds.
Slicing performed in 0 seconds.
Prediction performed in 0.7890589237213135 seconds.
Exporting performed in 0.041599273681640625 seconds.


In [9]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './custom_utils/annotations/subset_visdrone_test_data_50_medium_v1.json' --result_json_path './runs/predict/exp318/result.json'

loading annotations into memory...
Done (t=0.00s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=0.34s).
Accumulating evaluation results...
DONE (t=0.02s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.101
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.176
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.099
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.081
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.358
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.645
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.036
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.207
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

#### **Orginal Adaptive-NMS**

In [19]:
def predict_fine_sliced_images_refactored_nms(input_folder, dataset_json_path, detection_model, base_slice_size=512):
    name = "exp"
    save_dir = Path(increment_path(Path("sliced_predictions") / name, exist_ok=False))
    os.makedirs(save_dir, exist_ok=True)

    if dataset_json_path:
        with open(dataset_json_path, "r") as file:
            data = json.load(file)
        
    vis_params = {
        "bbox_thickness": 2,
        "text_size": 0.5,
        "text_thickness": 1,
        "hide_labels": False,
        "hide_conf": False,
        "format": "png"
    }

    image_files = [
        f for f in os.listdir(input_folder)
        if f.lower().endswith((".jpg", ".jpeg", ".png"))
    ]

    print(f"\nRunning fine slicing prediction on {len(image_files)} image(s)...")
    total_prediction_time = 0.0
    grand_total_predictions = 0
    all_coco_preds = []

    for filename in image_files:
        image_path = os.path.join(input_folder, filename)
        image_pil = Image.open(image_path).convert("RGB")
        image_np = np.array(image_pil)
        image_h, image_w = image_np.shape[:2]
        filename_wo_ext = Path(filename).stem
        total_prediction_count = 0
        print("*****************************************")
        print("File Name", filename_wo_ext)

        img_id = get_image_id(data, filename_wo_ext) if dataset_json_path else None
        all_object_predictions = []
        count = 0

        # Split image into 2x2 grid
        grid_h, grid_w = image_h // 2, image_w // 2

        for row in range(2):
            for col in range(2):
                x1, y1 = col * grid_w, row * grid_h
                x2, y2 = min(x1 + grid_w, image_w), min(y1 + grid_h, image_h)
                sub_img = image_pil.crop((x1, y1, x2, y2))
                print("Cropped Image:", x1, y1, x2, y2)

                time_start = time.time()
                base_pred = get_prediction(sub_img, detection_model)
                time_end = time.time() - time_start
                print("Initial Prediction time is: {:.2f} ms".format(time_end * 1000))

                coarse_preds = base_pred.object_prediction_list
                object_density = len(coarse_preds)
                print("Object Density:", object_density)

                slice_params = get_slice_parameters(object_density, base_slice_size)

                iteration_time = time_end

                preds = coarse_preds.copy()

                if slice_params:
                    slice_width, slice_height, overlap_w, overlap_h = slice_params
                    print("********* Slice Parameters ***********")
                    print("Slice Width: ", slice_width)
                    print("Slice Height: ", slice_height)
                    print("Overlap Width Ratio: ", overlap_w)
                    print("Overlap Height Ratio: ", overlap_h)

                    time_start_slice = time.time()
                    sliced_pred = get_sliced_prediction(
                        sub_img,
                        detection_model,
                        slice_height=slice_height,
                        slice_width=slice_width,
                        overlap_height_ratio=overlap_h,
                        overlap_width_ratio=overlap_w,
                        postprocess_type="NMS",
                        postprocess_match_metric="IOU",
                        postprocess_match_threshold=0.3,
                        postprocess_min_area=16,
                        verbose=0
                    )
                    time_end_slice = time.time() - time_start_slice
                    print("Sliced Prediction time is: {:.2f} ms".format(time_end_slice * 1000))
                    
                    iteration_time += time_end_slice
                    fine_preds = sliced_pred.object_prediction_list
                    print("Pre Slicing: ", len(preds))
                    preds.extend(fine_preds)
                    print("Post Slicing: ", len(preds))
                else:
                    print("Prediction time is: {:.2f} ms".format(time_end * 1000))
                    #preds = base_pred.object_prediction_list

                # Offset bounding boxes back to original image space
                #print("Total Prediction for single image: ", len(preds))
                for pred in preds:
                    count += 1
                    print("Count:", count)
                    pred.bbox.minx += x1
                    pred.bbox.maxx += x1
                    pred.bbox.miny += y1
                    pred.bbox.maxy += y1
                    all_object_predictions.append(pred)

                total_prediction_count += len(preds)
                total_prediction_time += iteration_time

        print("________________________________________________")

        # Merge all predictions for image
        merged_preds = apply_nms(all_object_predictions, iou_threshold=0.5)
        
        #object_prediction_list = ObjectPredictionList(all_object_predictions)
        #merged_keep = truncated_nms_merge(object_prediction_list.totensor())
        #selected_object_predictions = object_prediction_list[merged_keep].tolist()
        #if not isinstance(selected_object_predictions, list):
        #    selected_object_predictions = [selected_object_predictions]
        
        # Convert merged predictions to COCO format
        if dataset_json_path:
            coco_preds = merged_preds_to_coco(merged_preds, img_id)
            all_coco_preds.extend(coco_preds)
            
        # Visualization
        visualize_object_predictions(
            image=np.ascontiguousarray(image_pil),
            object_prediction_list=merged_preds,
            rect_th=vis_params["bbox_thickness"],
            text_size=vis_params["text_size"],
            text_th=vis_params["text_thickness"],
            hide_labels=vis_params["hide_labels"],
            hide_conf=vis_params["hide_conf"],
            output_dir=save_dir,
            file_name=filename_wo_ext,
            export_format=vis_params["format"]
        )

        grand_total_predictions += total_prediction_count

    if dataset_json_path:
        save_path = str(save_dir / "result.json")
        save_json(all_coco_preds, save_path)
   
    print(f"\nCompleted {len(image_files)} images.")
    print("Total Prediction Count (Before NMS Merge): ", grand_total_predictions)
    print("Total Prediction Count (After Final NMS Merge): ", len(all_coco_preds))
    print("Total Prediction time for all images is: {:.2f} ms".format(total_prediction_time * 1000))
    print(f"Prediction results are successfully exported to {save_dir}")


In [12]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
source_folder = './single_test/images'
json_path = "./subset_visdrone_test_990.json"
slice_size = 256

# Run fine-sliced adaptive prediction
result = predict_fine_sliced_images_refactored_nms(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=detection_model,
    base_slice_size=slice_size              
)


Running fine slicing prediction on 1 image(s)...
*****************************************
File Name 0000006_06773_d_0000018
Cropped Image: 0 0 680 382
Initial Prediction time is: 8.31 ms
Object Density: 15
********* Slice Parameters ***********
Slice Width:  256
Slice Height:  256
Overlap Width Ratio:  0.15
Overlap Height Ratio:  0.15
Sliced Boxes Count: 6
POST PROCESS:  NMS
Original Prediction Count 39
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  15
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  3
Final Bounding Box Count (NMS):  1
Sliced Prediction time is: 58.89 ms
Pre Slicing:  15
Post Slicing:  36
Count: 1
Count: 2
Count: 3
Count: 4
Count: 5
Count: 6
Count: 7
Count: 8
Count: 9
Count: 10
Count: 11
Count: 12
Count: 13
Count: 14
Count: 15
Count: 16
Count: 17
Count: 18
Count: 19
Count: 20
Count: 21
Count: 22
Count: 23
Count: 24
Count: 25
Count: 26
Count: 27
Count: 28
Count: 29
Count: 30
Count: 31
Count: 32
Count: 33
Count: 34
Count: 35
Cou

In [30]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './subset_visdrone_test_990.json' --result_json_path './sliced_predictions/exp516/result.json'

loading annotations into memory...
Done (t=0.00s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=0.01s).
Accumulating evaluation results...
DONE (t=0.00s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.429
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.772
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.493
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.976
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.770
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.574
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.435
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.488
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

In [20]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
source_folder = './test_subsets/v5/images'
json_path = "./subset_visdrone_test_data_15_v5.json"
slice_size = 256

# Run fine-sliced adaptive prediction
result = predict_fine_sliced_images_refactored_nms(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=detection_model,
    base_slice_size=slice_size              
)


Running fine slicing prediction on 15 image(s)...
*****************************************
File Name 9999963_00000_d_0000057
Cropped Image: 0 0 700 525
Initial Prediction time is: 11.25 ms
Object Density: 3
Prediction time is: 11.25 ms
Count: 1
Count: 2
Count: 3
Cropped Image: 700 0 1400 525
Initial Prediction time is: 8.76 ms
Object Density: 20
********* Slice Parameters ***********
Slice Width:  256
Slice Height:  256
Overlap Width Ratio:  0.15
Overlap Height Ratio:  0.15
Sliced Boxes Count: 12
POST PROCESS:  NMS
Original Prediction Count 31
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  18
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  1
Sliced Prediction time is: 107.75 ms
Pre Slicing:  20
Post Slicing:  42
Count: 4
Count: 5
Count: 6
Count: 7
Count: 8
Count: 9
Count: 10
Count: 11
Count: 12
Count: 13
Count: 14
Count: 15
Count: 16
Count: 17
Count: 18
Count: 19
Count: 20
Count: 21
Count: 22
Count: 23
Count:

In [21]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './subset_visdrone_test_data_15_v5.json' --result_json_path './sliced_predictions/exp546/result.json'

loading annotations into memory...
Done (t=0.00s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=0.17s).
Accumulating evaluation results...
DONE (t=0.01s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.135
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.218
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.147
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.168
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.278
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.300
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.088
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.175
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

In [51]:
result_predict_nms = predict(source='./single_test/images_bbk',
                         dataset_json_path = './subset_vis_test_data_1563.json',
                         model_type = 'ultralytics',
                         model_path = 'models/yolov8/last.pt',
                         slice_height = 256,
                         slice_width = 256,
                         overlap_height_ratio = 0.5,
                         overlap_width_ratio = 0.5,
                         postprocess_type = "NMS",
                         postprocess_min_area = 16,
                         postprocess_conf_threshold = 0.3,                  
                         verbose = 2
                        )

POST PROCESSING: NMS
indexing coco dataset annotations...


Performing inference on images:   0%|          | 0/1 [00:00<?, ?it/s]

Image Name: 0000078_03171_d_0000009
Image Size:  (1360, 765)
Sliced Boxes Count: 50
POST PROCESS:  NMS
Performing prediction on 50 slices.


Performing inference on images: 100%|██████████| 1/1 [00:00<00:00,  1.60it/s]

Original Prediction Count 311
Final Bounding Box Count (NMS):  19
Final Bounding Box Count (NMS):  2
Final Bounding Box Count (NMS):  22
Final Bounding Box Count (NMS):  3
Final Bounding Box Count (NMS):  43
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  2
Prediction time is: 507.96 ms
Prediction results are successfully exported to runs/predict/exp304
Model loaded in 0.03128695487976074 seconds.
Slicing performed in 0.001195669174194336 seconds.
Prediction performed in 0.5079617500305176 seconds.
Exporting performed in 0.048369407653808594 seconds.


In [48]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
source_folder = './single_test/images_bbk/images'
json_path = "./subset_vis_test_data_1563.json"
slice_size = 256

# Run fine-sliced adaptive prediction
result = predict_fine_sliced_images_refactored_nms(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=detection_model,
    base_slice_size=slice_size              
)


Running fine slicing prediction on 1 image(s)...
*****************************************
File Name 0000078_03171_d_0000009
Cropped Image: 0 0 680 382
Initial Prediction time is: 10.88 ms
Object Density: 25
********* Slice Parameters ***********
Slice Width:  256
Slice Height:  256
Overlap Width Ratio:  0.25
Overlap Height Ratio:  0.25
Sliced Boxes Count: 8
POST PROCESS:  NMS
Original Prediction Count 90
Final Bounding Box Count (NMS):  9
Final Bounding Box Count (NMS):  6
Final Bounding Box Count (NMS):  2
Final Bounding Box Count (NMS):  23
Final Bounding Box Count (NMS):  1
Sliced Prediction time is: 81.74 ms
Pre Slicing:  25
Post Slicing:  66
Count: 1
Count: 2
Count: 3
Count: 4
Count: 5
Count: 6
Count: 7
Count: 8
Count: 9
Count: 10
Count: 11
Count: 12
Count: 13
Count: 14
Count: 15
Count: 16
Count: 17
Count: 18
Count: 19
Count: 20
Count: 21
Count: 22
Count: 23
Count: 24
Count: 25
Count: 26
Count: 27
Count: 28
Count: 29
Count: 30
Count: 31
Count: 32
Count: 33
Count: 34
Count: 35
Co

In [49]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './subset_vis_test_data_1563.json' --result_json_path './sliced_predictions/exp536/result.json'

loading annotations into memory...
Done (t=0.00s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=0.03s).
Accumulating evaluation results...
DONE (t=0.01s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.186
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.407
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.198
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.237
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.655
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 1.000
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.093
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.327
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

In [52]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './subset_vis_test_data_1563.json' --result_json_path './runs/predict/exp304/result.json'

loading annotations into memory...
Done (t=0.00s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=0.03s).
Accumulating evaluation results...
DONE (t=0.01s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.141
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.257
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.131
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.220
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.385
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.835
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.084
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.148
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

In [23]:
result_predict_nms = predict(source='./test_subsets/v5',
                         dataset_json_path = './subset_visdrone_test_data_15_v5.json',
                         model_type = 'ultralytics',
                         model_path = 'models/yolov8/last.pt',
                         slice_height = 256,
                         slice_width = 256,
                         overlap_height_ratio = 0.5,
                         overlap_width_ratio = 0.5,
                         postprocess_type = "NMS",
                         postprocess_min_area = 16,
                         postprocess_conf_threshold = 0.3,                  
                         verbose = 2
                        )

POST PROCESSING: NMS
indexing coco dataset annotations...


Performing inference on images:   0%|          | 0/15 [00:00<?, ?it/s]

Image Name: 9999963_00000_d_0000057
Image Size:  (1400, 1050)
Sliced Boxes Count: 80
POST PROCESS:  NMS
Performing prediction on 80 slices.


Performing inference on images:   7%|▋         | 1/15 [00:00<00:12,  1.13it/s]

Original Prediction Count 120
Final Bounding Box Count (NMS):  5
Final Bounding Box Count (NMS):  30
Final Bounding Box Count (NMS):  5
Final Bounding Box Count (NMS):  5
Final Bounding Box Count (NMS):  6
Final Bounding Box Count (NMS):  1
Prediction time is: 742.08 ms
Image Name: 9999963_00000_d_0000006
Image Size:  (1400, 1050)
Sliced Boxes Count: 80
POST PROCESS:  NMS
Performing prediction on 80 slices.


...

Original Prediction Count 221
Final Bounding Box Count (NMS):  3
Final Bounding Box Count (NMS):  45
Final Bounding Box Count (NMS):  6
Final Bounding Box Count (NMS):  9
Final Bounding Box Count (NMS):  6
Final Bounding Box Count (NMS):  4
Prediction time is: 528.31 ms
Image Name: 9999952_00000_d_0000216
Image Size:  (1400, 788)
Sliced Boxes Count: 60
POST PROCESS:  NMS
Performing prediction on 60 slices.


Performing inference on images:  93%|█████████▎| 14/15 [00:09<00:00,  1.50it/s]

Original Prediction Count 121
Final Bounding Box Count (NMS):  5
Final Bounding Box Count (NMS):  18
Final Bounding Box Count (NMS):  5
Final Bounding Box Count (NMS):  6
Final Bounding Box Count (NMS):  7
Final Bounding Box Count (NMS):  3
Prediction time is: 518.37 ms
Image Name: 9999938_00000_d_0000124
Image Size:  (1400, 788)
Sliced Boxes Count: 60
POST PROCESS:  NMS
Performing prediction on 60 slices.


Performing inference on images: 100%|██████████| 15/15 [00:10<00:00,  1.43it/s]

Original Prediction Count 46
Final Bounding Box Count (NMS):  4
Final Bounding Box Count (NMS):  9
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  3
Final Bounding Box Count (NMS):  1
Prediction time is: 508.48 ms
Prediction results are successfully exported to runs/predict/exp306
Model loaded in 0.0332331657409668 seconds.
Slicing performed in 0.022745370864868164 seconds.
Prediction performed in 8.639551162719727 seconds.
Exporting performed in 0.0503535270690918 seconds.


In [24]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './subset_visdrone_test_data_15_v5.json' --result_json_path './runs/predict/exp306/result.json'

loading annotations into memory...
Done (t=0.00s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=0.19s).
Accumulating evaluation results...
DONE (t=0.01s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.141
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.254
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.151
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.185
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.257
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.650
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.082
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.151
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

#### **Dense Images**

In [55]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
# Using Different IoU threshold
source_folder = './custom_utils/testdev_subsets/dense/v1/images'
json_path = "./custom_utils/annotations/subset_visdrone_test_data_50_dense_v1.json"
slice_size = 256

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=detection_model,
    base_slice_size=slice_size              
)


Running fine slicing prediction on 50 image(s)...
*****************************************
File Name:  9999979_00000_d_0000047
*****************************************
Base pred time: 35.55 ms
Total Based pred time: 35.55 ms
Full Image Object Density: 72
Cropped Image Dimension: 0 0 700 525
Initial Prediction time is: 9.87 ms
Slice Object Density: 37
********* Slice Parameters ***********
Slice Width:  256
Slice Height:  256
Overlap Width Ratio:  0.25
Overlap Height Ratio:  0.25
Sliced Boxes Count: 12
POST PROCESS:  NMS
Original Prediction Count 151
Final Bounding Box Count (NMS):  3
Final Bounding Box Count (NMS):  45
Final Bounding Box Count (NMS):  8
Final Bounding Box Count (NMS):  2
Final Bounding Box Count (NMS):  1
Sliced Prediction time is: 118.43 ms
Pre Adaptive Slicing:  37
Post Adaptive Slicing:  96
Cropped Image Dimension: 700 0 1400 525
Initial Prediction time is: 8.26 ms
Slice Object Density: 1
Prediction time is: 8.26 ms
Cropped Image Dimension: 0 525 700 1050
Initial

In [57]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './custom_utils/annotations/subset_visdrone_test_data_50_dense_v1.json' --result_json_path './sliced_predictions/exp556/result.json'

loading annotations into memory...
Done (t=0.06s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=3.19s).
Accumulating evaluation results...
DONE (t=0.04s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.133
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.229
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.132
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.169
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.351
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.530
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.085
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.209
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

In [12]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
# Using Different IoU threshold
source_folder = './custom_utils/testdev_subsets/dense/v1/images'
json_path = "./custom_utils/annotations/subset_visdrone_test_data_50_dense_v1.json"
slice_size = 128

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=detection_model,
    base_slice_size=slice_size              
)


Running fine slicing prediction on 50 image(s)...
*****************************************
File Name:  9999979_00000_d_0000047
*****************************************
Base pred time: 30.39 ms
Total Based pred time: 30.39 ms
Full Image Object Density: 72
Cropped Image Dimension: 0 0 700 525
Initial Prediction time is: 9.28 ms
Slice Object Density: 37
********* Slice Parameters ***********
Slice Width:  128
Slice Height:  128
Overlap Width Ratio:  0.25
Overlap Height Ratio:  0.25
Sliced Boxes Count: 42
POST PROCESS:  NMS
Original Prediction Count 131
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  63
Final Bounding Box Count (NMS):  3
Final Bounding Box Count (NMS):  4
Final Bounding Box Count (NMS):  1
Sliced Prediction time is: 282.87 ms
Pre Adaptive Slicing:  37
Post Adaptive Slicing:  109
Cropped Image Dimension: 700 0 1400 525
Initial Prediction time is: 8.14 ms
Slice Object Density: 1
Prediction time is: 8.14 ms
Cropped Image Dimension: 0 525 700 1050
Initia

In [13]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './custom_utils/annotations/subset_visdrone_test_data_50_dense_v1.json' --result_json_path './sliced_predictions/exp558/result.json'

loading annotations into memory...
Done (t=0.06s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=3.13s).
Accumulating evaluation results...
DONE (t=0.04s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.112
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.188
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.112
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.120
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.336
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.539
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.059
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.203
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

In [14]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
# Using Different IoU threshold
source_folder = './custom_utils/testdev_subsets/dense/v1/images'
json_path = "./custom_utils/annotations/subset_visdrone_test_data_50_dense_v1.json"
slice_size = 64

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=detection_model,
    base_slice_size=slice_size              
)


Running fine slicing prediction on 50 image(s)...
*****************************************
File Name:  9999979_00000_d_0000047
*****************************************
Base pred time: 37.09 ms
Total Based pred time: 37.09 ms
Full Image Object Density: 72
Cropped Image Dimension: 0 0 700 525
Initial Prediction time is: 9.42 ms
Slice Object Density: 37
********* Slice Parameters ***********
Slice Width:  64
Slice Height:  64
Overlap Width Ratio:  0.25
Overlap Height Ratio:  0.25
Sliced Boxes Count: 165
POST PROCESS:  NMS
Original Prediction Count 55
Final Bounding Box Count (NMS):  41
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  1
Sliced Prediction time is: 958.19 ms
Pre Adaptive Slicing:  37
Post Adaptive Slicing:  80
Cropped Image Dimension: 700 0 1400 525
Initial Prediction time is: 8.65 ms
Slice Object Density: 1
Prediction time is: 8.65 ms
Cropped Image Dimension: 0 525 700 1050
Initial Prediction time is: 8.97 ms
Slice Object Density: 70
********* Slice Pa

In [15]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './custom_utils/annotations/subset_visdrone_test_data_50_dense_v1.json' --result_json_path './sliced_predictions/exp559/result.json'

loading annotations into memory...
Done (t=0.06s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=2.88s).
Accumulating evaluation results...
DONE (t=0.04s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.130
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.213
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.133
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.124
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.379
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.539
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.062
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.236
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

In [17]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
# Using Different IoU threshold
source_folder = './custom_utils/testdev_subsets/dense/v1/images'
json_path = "./custom_utils/annotations/subset_visdrone_test_data_50_dense_v1.json"
slice_size = 512

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=detection_model,
    base_slice_size=slice_size              
)


Running fine slicing prediction on 50 image(s)...
*****************************************
File Name:  9999979_00000_d_0000047
*****************************************
Base pred time: 35.46 ms
Total Based pred time: 35.46 ms
Full Image Object Density: 72
Cropped Image Dimension: 0 0 700 525
Initial Prediction time is: 9.42 ms
Slice Object Density: 37
********* Slice Parameters ***********
Slice Width:  512
Slice Height:  512
Overlap Width Ratio:  0.25
Overlap Height Ratio:  0.25
Sliced Boxes Count: 4
POST PROCESS:  NMS
Original Prediction Count 146
Final Bounding Box Count (NMS):  34
Final Bounding Box Count (NMS):  5
Sliced Prediction time is: 79.35 ms
Pre Adaptive Slicing:  37
Post Adaptive Slicing:  76
Cropped Image Dimension: 700 0 1400 525
Initial Prediction time is: 8.44 ms
Slice Object Density: 1
Prediction time is: 8.44 ms
Cropped Image Dimension: 0 525 700 1050
Initial Prediction time is: 8.76 ms
Slice Object Density: 70
********* Slice Parameters ***********
Slice Width:  

In [18]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './custom_utils/annotations/subset_visdrone_test_data_50_dense_v1.json' --result_json_path './sliced_predictions/exp560/result.json'

loading annotations into memory...
Done (t=0.06s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=2.66s).
Accumulating evaluation results...
DONE (t=0.03s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.158
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.268
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.158
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.192
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.404
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.536
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.097
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.247
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

#### **High Images**

In [9]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
# Using Different IoU threshold
source_folder = './custom_utils/testdev_subsets/high/v1/images'
json_path = "./custom_utils/annotations/subset_visdrone_test_data_50_high_v1.json"
slice_size = 256

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=detection_model,
    base_slice_size=slice_size              
)


Running fine slicing prediction on 50 image(s)...
*****************************************
File Name:  9999938_00000_d_0000372
*****************************************
Base pred time: 1581.03 ms
Total Based pred time: 1581.03 ms
Full Image Object Density: 35
Cropped Image Dimension: 0 0 700 394
Initial Prediction time is: 8.83 ms
Slice Object Density: 28
********* Slice Parameters ***********
Slice Width:  256
Slice Height:  256
Overlap Width Ratio:  0.25
Overlap Height Ratio:  0.25
Sliced Boxes Count: 8
POST PROCESS:  NMS
Original Prediction Count 97
Final Bounding Box Count (NMS):  30
Final Bounding Box Count (NMS):  18
Final Bounding Box Count (NMS):  2
Final Bounding Box Count (NMS):  8
Sliced Prediction time is: 82.87 ms
Pre Adaptive Slicing:  28
Post Adaptive Slicing:  86
Cropped Image Dimension: 700 0 1400 394
Initial Prediction time is: 7.38 ms
Slice Object Density: 6
Prediction time is: 7.38 ms
Cropped Image Dimension: 0 394 700 788
Initial Prediction time is: 6.86 ms
Slice

In [10]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './custom_utils/annotations/subset_visdrone_test_data_50_high_v1.json' --result_json_path './sliced_predictions/exp577/result.json'

loading annotations into memory...
Done (t=0.01s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=0.89s).
Accumulating evaluation results...
DONE (t=0.03s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.154
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.264
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.158
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.169
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.463
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.663
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.085
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.253
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

In [11]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
# Using Different IoU threshold
source_folder = './custom_utils/testdev_subsets/high/v1/images'
json_path = "./custom_utils/annotations/subset_visdrone_test_data_50_high_v1.json"
slice_size = 128

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=detection_model,
    base_slice_size=slice_size              
)


Running fine slicing prediction on 50 image(s)...
*****************************************
File Name:  9999938_00000_d_0000372
*****************************************
Base pred time: 26.89 ms
Total Based pred time: 26.89 ms
Full Image Object Density: 35
Cropped Image Dimension: 0 0 700 394
Initial Prediction time is: 8.49 ms
Slice Object Density: 28
********* Slice Parameters ***********
Slice Width:  128
Slice Height:  128
Overlap Width Ratio:  0.25
Overlap Height Ratio:  0.25
Sliced Boxes Count: 28
POST PROCESS:  NMS
Original Prediction Count 129
Final Bounding Box Count (NMS):  57
Final Bounding Box Count (NMS):  16
Final Bounding Box Count (NMS):  1
Final Bounding Box Count (NMS):  16
Sliced Prediction time is: 199.31 ms
Pre Adaptive Slicing:  28
Post Adaptive Slicing:  118
Cropped Image Dimension: 700 0 1400 394
Initial Prediction time is: 7.47 ms
Slice Object Density: 6
Prediction time is: 7.47 ms
Cropped Image Dimension: 0 394 700 788
Initial Prediction time is: 6.96 ms
Slic

In [12]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './custom_utils/annotations/subset_visdrone_test_data_50_high_v1.json' --result_json_path './sliced_predictions/exp578/result.json'

loading annotations into memory...
Done (t=0.01s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=1.12s).
Accumulating evaluation results...
DONE (t=0.03s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.146
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.246
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.149
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.116
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.483
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.664
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.051
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.270
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

In [13]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
# Using Different IoU threshold
source_folder = './custom_utils/testdev_subsets/high/v1/images'
json_path = "./custom_utils/annotations/subset_visdrone_test_data_50_high_v1.json"
slice_size = 64

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=detection_model,
    base_slice_size=slice_size              
)


Running fine slicing prediction on 50 image(s)...
*****************************************
File Name:  9999938_00000_d_0000372
*****************************************
Base pred time: 27.20 ms
Total Based pred time: 27.20 ms
Full Image Object Density: 35
Cropped Image Dimension: 0 0 700 394
Initial Prediction time is: 8.45 ms
Slice Object Density: 28
********* Slice Parameters ***********
Slice Width:  64
Slice Height:  64
Overlap Width Ratio:  0.25
Overlap Height Ratio:  0.25
Sliced Boxes Count: 120
POST PROCESS:  NMS
Original Prediction Count 82
Final Bounding Box Count (NMS):  49
Final Bounding Box Count (NMS):  17
Final Bounding Box Count (NMS):  3
Sliced Prediction time is: 701.70 ms
Pre Adaptive Slicing:  28
Post Adaptive Slicing:  97
Cropped Image Dimension: 700 0 1400 394
Initial Prediction time is: 7.44 ms
Slice Object Density: 6
Prediction time is: 7.44 ms
Cropped Image Dimension: 0 394 700 788
Initial Prediction time is: 6.92 ms
Slice Object Density: 0
Prediction time is:

In [14]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './custom_utils/annotations/subset_visdrone_test_data_50_high_v1.json' --result_json_path './sliced_predictions/exp579/result.json'

loading annotations into memory...
Done (t=0.01s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=1.03s).
Accumulating evaluation results...
DONE (t=0.03s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.162
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.268
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.167
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.127
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.499
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.664
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.057
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.282
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

In [15]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
# Using Different IoU threshold
source_folder = './custom_utils/testdev_subsets/high/v1/images'
json_path = "./custom_utils/annotations/subset_visdrone_test_data_50_high_v1.json"
slice_size = 512

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_images(
    input_folder=source_folder,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=detection_model,
    base_slice_size=slice_size              
)


Running fine slicing prediction on 50 image(s)...
*****************************************
File Name:  9999938_00000_d_0000372
*****************************************
Base pred time: 27.26 ms
Total Based pred time: 27.26 ms
Full Image Object Density: 35
Cropped Image Dimension: 0 0 700 394
Initial Prediction time is: 8.40 ms
Slice Object Density: 28
********* Slice Parameters ***********
Slice Width:  512
Slice Height:  512
Overlap Width Ratio:  0.25
Overlap Height Ratio:  0.25
Sliced Boxes Count: 2
POST PROCESS:  NMS
Original Prediction Count 69
Final Bounding Box Count (NMS):  22
Final Bounding Box Count (NMS):  7
Final Bounding Box Count (NMS):  2
Final Bounding Box Count (NMS):  3
Sliced Prediction time is: 108.30 ms
Pre Adaptive Slicing:  28
Post Adaptive Slicing:  62
Cropped Image Dimension: 700 0 1400 394
Initial Prediction time is: 7.52 ms
Slice Object Density: 6
Prediction time is: 7.52 ms
Cropped Image Dimension: 0 394 700 788
Initial Prediction time is: 6.94 ms
Slice Obj

In [16]:
#USING Adaptive-Optimized-NMS-IoU METHOD (NMS) --> min_area - 16
!sahi coco evaluate --dataset_json_path './custom_utils/annotations/subset_visdrone_test_data_50_high_v1.json' --result_json_path './sliced_predictions/exp580/result.json'

loading annotations into memory...
Done (t=0.01s)
creating index...
index created!

Evaluating bbox...
Loading and preparing results...
DONE (t=0.00s)
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=0.76s).
Accumulating evaluation results...
DONE (t=0.02s).
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=   all | maxDets=500 ] = 0.183
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=500 ] = 0.305
 Average Precision  (AP) @[ IoU=0.75      | area=   all | maxDets=500 ] = 0.183
 Average Precision  (AP) @[ IoU=0.50      | area= small | maxDets=500 ] = 0.195
 Average Precision  (AP) @[ IoU=0.50      | area=medium | maxDets=500 ] = 0.506
 Average Precision  (AP) @[ IoU=0.50      | area= large | maxDets=500 ] = 0.659
 Average Precision  (AP) @[ IoU=0.50:0.95 | area= small | maxDets=500 ] = 0.099
 Average Precision  (AP) @[ IoU=0.50:0.95 | area=medium | maxDets=500 ] = 0.284
 Average Precision  (AP) @[ IoU=0.50:0.95 | a

In [20]:
import gradio as gr
print(gr.__version__)

05/02/2025 17:00:24 - INFO - httpx -   HTTP Request: GET https://api.gradio.app/gradio-messaging/en "HTTP/1.1 200 OK"


4.44.1


In [5]:
def greeting(name):
    return "Hi !! This is "+name+"."

In [ ]:
interface = gr.Interface(
            fn=greeting, 
            inputs="text", 
            outputs="text")

In [25]:
# Gradio Interface Pipeline
#def gradio_pipeline(image_paths, model_name, confidence_threshold):
#    original_images, full_images, gois_images, metrics = process_images(image_paths, model_name, confidence_threshold)
#    metrics_table = pd.DataFrame(metrics).to_html(index=False, border=1, justify="center")
#    return metrics_table, original_images, full_images, gois_images

#model_category = ["yolo11n", "yolov10n", "yolov9n", "yolov8n"]
slice_sizes = [256, 128, 64]

# Gradio Interface Setup
with gr.Blocks() as interface:
    gr.Markdown("# Adaptive Multilevel Slicing Aided Hyper Inferance Approach")
    gr.Markdown("# Upload an image and select a model and confidence threshold to apply for the Adaptive Multilevel Slicing Aided Hyper Inferance")

    with gr.Row():
        image_input = gr.Image(type="filepath", label="Upload an Image")
        #model_dropdown = gr.Dropdown(choices=model_category, label="Select Model")
        slice_size_dropdown = gr.Dropdown(choices=slice_sizes, label="Select Slice Size")
        confidence_slider = gr.Slider(minimum=0.0, maximum=1.0, value=0.3, step=0.05, label="Confidence Threshold")
    
    predict_button = gr.Button("Run Prediction")

    with gr.Row():
        metrics_output = gr.HTML(label="Detection Metrics Table")
        original_gallery = gr.Gallery(label="Original Images")
        #full_gallery = gr.Gallery(label="Full Image Detections")
        adaptive_sahi__gallery = gr.Gallery(label="Adaptive-Multilevel-Sliced Image Detections")

    with gr.Tab("Detection Results"):
        with gr.Row():
            adaptive_image_output = gr.Image(type="pil", label="Adaptive Image Detection Result")
    
    predict_button.click(fn=predict_multilevel_fine_sliced_single_image, inputs=[image_input, detection_model, confidence_slider, slice_size_dropdown], outputs=[
        #full_image_output,
        adaptive_image_output
    ])
interface.launch(inline=True, share=True)


AttributeError: 'UltralyticsDetectionModel' object has no attribute '_id'

05/02/2025 17:11:00 - INFO - httpx -   HTTP Request: GET https://api.gradio.app/pkg-version "HTTP/1.1 200 OK"


In [15]:
# Example usage: Adaptive-Optimized-NMS Take 2(Adaptive-OptNMS)
image_path = './single_test/images_v1/0000006_07596_d_0000020.jpg'
json_path = "./subset_visdrone_test_data_952.json"
slice_size = 256

# Run fine-sliced adaptive prediction
result = predict_multilevel_fine_sliced_single_image(
    image_path=image_path,             # Folder with input images
    dataset_json_path=json_path,            # Optional: COCO JSON for ID mapping (or use None)
    detection_model=detection_model,
    base_slice_size=slice_size              
)


Running fine slicing prediction on single image...
*****************************************
File Name:  0000006_07596_d_0000020.jpg
*****************************************
Base pred time: 42.57 ms
Total Based pred time: 42.57 ms
Full Image Object Density: 11
Cropped Image Dimension: 0 0 680 382
Initial Prediction time is: 21.38 ms
Slice Object Density: 5
Prediction time is: 21.38 ms
Cropped Image Dimension: 680 0 1360 382
Initial Prediction time is: 21.43 ms
Slice Object Density: 3
Prediction time is: 21.43 ms
Cropped Image Dimension: 0 382 680 764
Initial Prediction time is: 20.78 ms
Slice Object Density: 3
Prediction time is: 20.78 ms
Cropped Image Dimension: 680 382 1360 764
Initial Prediction time is: 20.85 ms
Slice Object Density: 1
Prediction time is: 20.85 ms
________________________________________________
Total Prediction Count (Crop+Slice):  23
Total Prediction Count (Before NMS Merge):  23
Total Prediction Count (After Final NMS Merge):  17
Total Prediction time for all 